# Pipeline
1. Compute stationary tension for notes
1. Get normalized values
1. Compute Subharmonic tension for notes
1. Get normalized Values
1. Sum with weights

Compute stationary means evaluate a pipeline that normalizes results. Look at previous implementation, and see how can i
1. ~ add the difference as a parameter (the cap) ~ 
1. then add function of get normalized results for notes. 
1. This can at the sametime add the parameter for compute distributively (for triads and chords)
or use the against the fundamental alone. 
This is the pipeline for stationary tension normalized for values of r, and note names with intervals. 
Should return a df with the rankings provided, chords, the values, raw and normalized, with method name



Compute subharmonic tension for notes, 
1. Add normalization
1. Make it so it is modularized (i want with this method, this method this method. )
1. Should return a df with the rankings provided, chords, the values, raw and normalized, with method name


# Interharmonic modulation normalized (intervals)
Methods to try 
<a href="./ihm_chan.ipynb">Here you can find these methods for interharmonic</a>
1. Chan's method classic (without weights, no limits just normalize)
1. Chan's method capped (capped 170)
1. Chan's method (capped at 85)
1. Experimental method  (no cap, all ranges, no weights per harmonic, all_weights region equal)
1. Experimental method  (capped 170, all ranges, no weights per harmonic, all_weights region equal)
1. Experimental method  (capped 80, all ranges, no weights per harmonic, all_weights region equal)
1. Experimental method2  (no cap, all ranges, weights per harmonic, all_weights region equal)
1. Experimental method2 (capped 170, all ranges, weights per harmonic, all_weights region equal)
1. Experimental method2  (capped 80, all ranges, weights per harmonic, all_weights region equal)
1. Experimental method3  (no cap, all ranges, no weights per harmonic, all_weights region weighted)
1. Experimental method3  (capped 170, all ranges, no weights per harmonic, all_weights region weighted)
1. Experimental method3  (capped 80, all ranges, no weights per harmonic, all_weights region weighted)
1. Experimental method4  (no cap, all ranges, weights per harmonic, all_weights region equal)
1. Experimental method4  (capped 170, all ranges, weights per harmonic, all_weights region equal)
1. Experimental method4  (capped 80, all ranges, weights per harmonic, all_weights region equal)


### The plan is get biggest df and plot correlation

In [1]:
from psychoacoustic_tension_chan_module import interharmonic_module as ihm
from psychoacoustic_tension_chan_module import subharmonic_module as shm
import altair as alt
import pandas as pd

def normalized_interharmonic_modulations_pipeline(note_combinations_array,
                                                  chord_labels_array,
                                                  harmonics_considered=10,
                                                  values_of_r_ranges = [(0.95, 1.1),(1.5,2.8)],
                                                  apply_weights_to_individual_harmonic=False,
                                                  limit_delta_frequency=False,
                                                  frequency_threshold=170,
                                                  include_lower_bound=True,
                                                  distributive=False,
                                                  apply_weights_to_region=False,
                                                  weights_for_regions={
                                                        'red_region': 1,
                                                        'orange_region': 0.70,
                                                        'yellow_region': 0,
                                                        'green_region': 0
                                                    },
                                                    ):
    """

In [2]:

## Do intervals!

notes = ['G2','G#2','A2','A#2','B2','C3','C#3','D3','D#3','E3','F3','F#3','G3']

## generating intervals
intervals = []
for note in notes:
    intervals.append(['G2',note])

chord_labels_intervals = ['U', 'm2', 'M2', 'm3', 'M3', 'P4', 'TT', 'P5', 'm6', 'M6', 'm7', 'M7', '8v']

empirical_ranking_intervals = ['U','8v','P5','P4','M3','M6','m6','m3','TT','m7','M2','M7','m2']


## Triads to consider

triads=[
    # major
    ['C4', 'E4', 'G4'],
    ['C4', 'D#4','G#4'],
    ['C4', 'F4', 'A4'],
    #minor
    ['C4', 'D#4','G4'],
    ['C4', 'E4', 'A4'],
    ['C4', 'F4','G#4'],
    #Suspended
    ['C4', 'F4','G4'],
    ['C4', 'D4','G4'],
    ['C4', 'F4','A#4'],
    # Diminished,
    ['C4', 'D#4','F#4'],
    ['C4', 'D#4','A4'],
    ['C4', 'F#4','A4'],
    # augmented
    ['C4', 'E4','G#4'],
]
chord_labels_triads = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]

In [32]:

normed_values_columns = ['normed_values_only_modulations','normed_values_weighted_modulations_only','normed_values_normed_weighted_modulations']


def pipeline_for_interharmonic_normalized_tension_scores(note_combinations_array, chord_labels_array, distributive=[True, False]):
        # defining number of harmonics to consider
    harmonics_considered = [2,3,4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32]

    #define ranges for r_lower, r_upper
    values_of_r_ranges = [0.0,0.125,0.25,0.5,1.5,2.5,3.5,4.5,5.5,6.5,7.5,8.5,9.5,10.5,11.5,12.5]
    # values_of_r_ranges = [0.25,0.5,1.5,2.5,3.5,4.5,5.5,6.5,7.5,8.5,9.5,10.5,11.5,12.5]


    double_r_ranges = [(values_of_r_ranges[i], values_of_r_ranges[i+1]) for i in range(len(values_of_r_ranges)-1)]

    # Chan's method vanilla
    r_ranges = [(0.95, 1.1), (1.5, 2.8)]

    # defining caps
    # caps = [0,170,80]
    caps = [0]


    # defining if we want weights for each harmonic
    weights_on_harmonic =[True, False]

    # defining if we want weights for each region
    weights_on_region = [True, False]

    ## biggest df with all methods: with raw values
    biggest_df = pd.DataFrame()

    process_string = 'triads'

    if(len(note_combinations_array[0])==2):
        print('Now processing intervals')
        process_string= 'intervals'
        distributive = [True]


    ## df for correlation with method
    corr_df = pd.DataFrame()
    for harmonics in harmonics_considered:
        print(f'Now processing {harmonics} harmonics')
        
        

        # loop for each cap
        for cap in caps:
            for distributive_option in distributive:

            
                df_for_method = ihm.normalized_interharmonic_modulations_pipeline(
                    note_combinations_array=note_combinations_array,
                    chord_labels_array=chord_labels_array,
                    harmonics_considered=harmonics,
                    values_of_r_ranges=r_ranges,
                    
                    apply_weights_to_individual_harmonic=False,
                    limit_delta_frequency=True if cap != 0 else False,
                    frequency_threshold=cap,
                    distributive=distributive_option,
                    apply_weights_to_region=False,
                    weights_for_regions={
                            'red_region': 1,
                            'orange_region': 1,
                            'yellow_region': 1,
                            'green_region': 1
                        },)
                df_for_method['method'] = f"Chan's method Vanilla Cap {cap} with  {'distributive' if distributive_option is True else 'non-distributive'}"
                df_for_method['harmonics_considered'] = harmonics
                biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
                

                ## Now loop if weights
                for weights_harmonic in weights_on_harmonic:
                    for weights_region in weights_on_region:
                        df_for_method = ihm.normalized_interharmonic_modulations_pipeline(
                            note_combinations_array=note_combinations_array,
                            chord_labels_array=chord_labels_array,
                            harmonics_considered=harmonics,
                            values_of_r_ranges=double_r_ranges,
                            
                            apply_weights_to_individual_harmonic=weights_harmonic,
                            limit_delta_frequency=True if cap != 0 else False,
                            frequency_threshold=cap,
                            distributive=True,
                            apply_weights_to_region=weights_region,
                            weights_for_regions={
                                    'red_region': 1,
                                    'orange_region': 0.7,
                                    'yellow_region': 0,
                                    'green_region': 0
                                },)
                        method_name = f"Experimental_methods's  {'with' if weights_harmonic is True else 'without'} weights on harmonics {'and' if weights_region is True else 'without'} weights on regions and {'distributive' if distributive_option is True else 'non-distributive'} Cap {cap}"
                        df_for_method['method'] = method_name
                        df_for_method['harmonics_considered'] = harmonics
                        biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)

    biggest_df.to_csv(f'overall_interharmonic_normalized_tension_scores_all_methods_{process_string}.csv', index=False)
    return biggest_df
            

            


In [33]:


            
        
   

biggest_df = pipeline_for_interharmonic_normalized_tension_scores(note_combinations_array=intervals, chord_labels_array=chord_labels_intervals)


    



Now processing intervals
Now processing 2 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 3 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:71: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 4 harmonics


...

C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 31 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 32 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\3541381349.py:97: FutureWarning: The behavior of DataFrame concatenation with em

In [34]:
biggest_df[biggest_df['method']=="Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0"]

note_combination chord_label  \
52              G2,E3          M6   
53              G2,F3          m7   
54             G2,F#3          M7   
55              G2,G3          8v   
56              G2,G2           U   
...               ...         ...   
2010            G2,B2          M3   
2011           G2,A#2          m3   
2012            G2,A2          M2   
2013            G2,G2           U   
2014           G2,G#2          m2   

                             raw_values_per_combination  \
52      [[0, 0, 0, 0, 0, 1, 0, 0, 0, 2, 0, 0, 0, 0, 0]]   
53      [[0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0]]   
54      [[0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0, 0]]   
55      [[1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0]]   
56      [[2, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 2, 0, 0, 0]]   
...                                                 ...   
2010  [[3, 9, 12, 51, 54, 48, 75, 62, 68, 51, 62, 57...   
2011  [[6, 7, 12, 55, 52, 68, 63, 59, 63, 56, 59, 58...   
2012  [[7, 6, 15, 54, 66, 61, 63, 57, 58, 57, 61, 56...   
2013  [[32, 0, 0, 60, 64, 62, 56, 58, 60, 56, 58, 60...   
2014  [[6, 7, 17, 61, 59, 60, 64, 58, 64, 53, 61, 58...   

     weighted_modulations_per_region_in_note_combinations  \
52                                                 None     
53                                                 None     
54                                                 None     
55                                                 None     
56                                                 None     
...                                                 ...     
2010                                               None     
2011                                               None     
2012                                               None     
2013                                               None     
2014                                               None     

     weighted_sum_per_region_normalized_tension_value  \
52                                               None   
53                                               None   
54                                               None   
55                                               None   
56                                               None   
...                                               ...   
2010                                             None   
2011                                             None   
2012                                             None   
2013                                             None   
2014                                             None   

      raw_t_score_summed_only_modulations  \
52                                    3.0   
53                                    3.0   
54                                    3.0   
55                                    3.0   
56                                    4.0   
...                                   ...   
2010                                723.0   
2011                                726.0   
2012                                728.0   
2013                                730.0   
2014                                731.0   

      raw_t_score_summed_using_weighted_normalized_value  \
52                                                  NaN    
53                                                  NaN    
54                                                  NaN    
55                                                  NaN    
56                                                  NaN    
...                                                 ...    
2010                                                NaN    
2011                                                NaN    
2012                                                NaN    
2013                                                NaN    
2014                                                NaN    

      raw_t_score_summed_using_weighted_modulations_no_norm  \
52                                                  NaN       
53                                           

## Now for interharmonic dataframe we have method, harmonics considered, normed values for interharmonic. Plan is to get reanking for each norm method and method and harmonics. 

In [35]:

from scipy.stats import pearsonr
normed_values_columns = ['normed_values_only_modulations','normed_values_weighted_modulations_only','normed_values_normed_weighted_modulations']
empirical_ranking_intervals = ['U','8v','P5','P4','M3','M6','m6','m3','TT','m7','M2','M7','m2']


def get_correlation_between_empirical_and_method(empirical_ranking, df_with_rankings, numbered_ranking=None,chord_label_column='chord_label', column_to_compare_with_emp='raw_t_score_summed_only_modulations'):
    ## first normalize empirical ranking

    empirical_ranking_numbered = range(0, len(empirical_ranking))

    if numbered_ranking is None:
        normalized_values = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]
    else:
        mininum = min(numbered_ranking) 
        maximum = max(numbered_ranking)
        normalized_values = [(x - mininum) / (maximum - mininum) for x in numbered_ranking]

    ## we are going to create a dictionary with the chord labels
    # with their respective scores. The plan is to see how correlated they are. 
    keys_for_dict = df_with_rankings[chord_label_column].tolist()
    
    ranked_df = {}
    for key in keys_for_dict:
        ranked_df[key] = df_with_rankings[df_with_rankings[chord_label_column] == key][column_to_compare_with_emp].values[0]
    
    ## now we are going to construct a list based on the empirical ranking 
    # using this dictionary

    for chord in empirical_ranking:
        if chord not in ranked_df.keys():
            print(f'Warning: chord {chord} not found in the dataframe keys')
            continue
    values_to_correlate = [ranked_df[chord] for chord in empirical_ranking]

    # get correlation
    corr, p_value = pearsonr(normalized_values, values_to_correlate)

    return corr, p_value, values_to_correlate


def break_into_different_rankings(biggest_df,empirical_ranking=[],numbered_ranking=None, method_column='method',x_axis='harmonics_considered', normed_values_columns=normed_values_columns):
    ## Now for interharmonic dataframe we have method, harmonics considered, normed values for interharmonic. Plan is to get reanking for each norm method and method and harmonics. 
    
    new_df= pd.DataFrame()
    ## break_into_methods first

    for different_method in biggest_df[method_column].unique():
        df_for_method = biggest_df[biggest_df[method_column] == different_method]
        # print(f'Now processing method {different_method}')
        # print(df_for_method)
        
        # print('----------------------------------')        

        ## after getting method, we need to get ranking order for each harmonics considered
        for harmonics in df_for_method[x_axis].unique():



            new_df_for_harmonics = df_for_method[df_for_method[x_axis] == harmonics]

            # print(f'Now processing harmonics {type(harmonics)}')
            # print(new_df_for_harmonics)
            # print('----------------------------------')


            # now we believe to have method and each harmonic. Now we need to rank for each
            # normed values column. We can do this by sorting values based on each column,
            # then assigning rank based on index position
            for normed_column in normed_values_columns:

                # print(f'Now processing normed column {normed_column}')
            
                # print(different_method, harmonics, normed_column)
                # print(type(different_method), type(harmonics), type(normed_column))
                

                ## Now for each normed column we are going to get correlation with empirical ranking
                # temp_df = pd.DataFrame()
                # temp_df['method'] = different_method
                # temp_df['harmonics_considered'] = harmonics
                # temp_df['normed_column'] = normed_column

                corr, p_value, values_to_correlate = get_correlation_between_empirical_and_method(empirical_ranking, df_with_rankings=new_df_for_harmonics, numbered_ranking=numbered_ranking, chord_label_column='chord_label', column_to_compare_with_emp=normed_column)

                # temp_df['correlation'] = corr
                # temp_df['p_value'] = p_value
                # temp_df['final_ranking_correlate'] = [values_to_correlate]

                temp_df = pd.DataFrame({
                    'method': [different_method + ' ' + normed_column],
                    'harmonics_considered': [harmonics],
                    'normed_column': [normed_column],
                    'correlation': [corr],
                    'p_value': [p_value],
                    'final_ranking_correlate': [values_to_correlate]
                })
                # print(temp_df)
                

                

                new_df = pd.concat([new_df, temp_df], ignore_index=True)

    return new_df





In [36]:
new_df = break_into_different_rankings(biggest_df,empirical_ranking=empirical_ranking_intervals, method_column='method',x_axis='harmonics_considered', normed_values_columns=normed_values_columns)

In [37]:
new_df.method.unique()

array(["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Chan's method Vanilla Cap 0 with  distributive normed_values_weighted_modulations_only",
       "Chan's method Vanilla Cap 0 with  distributive normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_weighted_modulations_o

In [38]:
df_to_work_with = new_df.dropna()


In [39]:
df_to_work_with.to_csv('overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv', index=False)

In [40]:
df_to_work_with = new_df.dropna()
df_to_work_with.to_csv('overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv', index=False)

In [41]:
df_to_work_with = pd.read_csv('overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv')

## Intervals Interharmonic corr heatmap

In [189]:
### cleaning unnecessary methods
df_chan = df_to_work_with['method'].str.contains('Chan')
df_to_work_with.method.unique()


array(["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
       "Experimental_methods's  without weights on 

In [13]:
df_exp_no_only = df_to_work_with['method'].str.contains("normed_weighted_modulations")
exception = df_to_work_with['method'].str.contains("without weights on regions")
# dimelo = df_to_work_with[df_exp_no_only]
# dimelo.method.unique()

In [18]:
mapping_to_new_names = {"Chan's method": "Method A",
       "Experimental_methods's  with weights on harmonics and weights on regions ":"Method E",
       "Experimental_methods's  with weights on harmonics without weights on regions ":"Method D",
       "Experimental_methods's  without weights on harmonics and weights on regions ":"Method C",
       "Experimental_methods's  without weights on harmonics without weights on regions ":"Method B"}
### cleaning unnecessary methods
df_chan = df_to_work_with['method'].str.contains('Chan')
df_to_work_with.method.unique()
df_exp_no_only = df_to_work_with['method'].str.contains("normed_weighted_modulations")
exception = df_to_work_with['method'].str.contains("without weights on regions")

new_df['method'] = new_df['method'].map(mapping_to_new_names)
new_df.method.unique()

new_df = df_to_work_with[(df_exp_no_only)|df_chan |exception]

## cleaning method names for better visualization
new_df['method'] = new_df['method'].str.replace("Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations","Chan's method")
new_df['method'] = new_df['method'].str.replace("and distributive Cap 0 normed_values_only_modulations","")
new_df['method'] = new_df['method'].str.replace("and distributive Cap 0 normed_values_normed_weighted_modulations","",regex=True)
new_df['method'].unique()


C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\1386403564.py:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['method'] = new_df['method'].str.replace("Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations","Chan's method")
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\1386403564.py:19: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['method'] = new_df['method'].str.replace("and distributive Cap 0 normed_values_only_modulations","")
C:\Users\gabri\AppData\Local\Te

array(["Chan's method",
       "Experimental_methods's  with weights on harmonics and weights on regions ",
       "Experimental_methods's  with weights on harmonics without weights on regions ",
       "Experimental_methods's  without weights on harmonics and weights on regions ",
       "Experimental_methods's  without weights on harmonics without weights on regions "],
      dtype=object)

In [19]:
mapping_to_new_names = {"Chan's method": "Method A",
       "Experimental_methods's  with weights on harmonics and weights on regions ":"Method E",
       "Experimental_methods's  with weights on harmonics without weights on regions ":"Method D",
       "Experimental_methods's  without weights on harmonics and weights on regions ":"Method C",
       "Experimental_methods's  without weights on harmonics without weights on regions ":"Method B"}
new_df['method'] = new_df['method'].map(mapping_to_new_names)
new_df.method.unique()

C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\2230183771.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['method'] = new_df['method'].map(mapping_to_new_names)


array(['Method A', 'Method E', 'Method D', 'Method C', 'Method B'],
      dtype=object)

In [20]:
subset_df = new_df[new_df['harmonics_considered']<=18]

corr_chart,text_chart = ihm.create_corr_heatmap(subset_df, x='harmonics_considered', y='method',  p_value_column='p_value', corr_column='correlation')

# corr_chart = corr_chart.encode(x=alt.X('harmonics_considered', title='Harmonics considered to compute Interharmonic Modulation',scale=alt.Scale(domain=[2,26],clamp=True)))
# text_chart = text_chart.encode(x=alt.X('harmonics_considered', title='Harmonics considered to compute Interharmonic Modulation',scale=alt.Scale(domain=[2,26],clamp=True)))
interval_chart = (corr_chart+text_chart).properties(width=600, height=170,title='Correlation between Empirical and Computed tension rankings for Intervals')
interval_chart


alt.LayerChart(...)

In [21]:
from pathlib import Path
import json

Path.cwd() / 'charts'

WindowsPath('c:/Users/gabri/OneDrive/Documents/Tension_visualization_tool/psychoacoustic_tension_science/charts')

In [22]:
interval_chart.save(Path.cwd() / 'charts' / 'ihm_corr_chart_intervals.json')

In [23]:
with open(Path.cwd() / 'charts' / 'ihm_corr_chart_intervals.json') as charjson:
    chart_2 = alt.Chart.from_dict(json.load(charjson))

    
    # chart_2 = alt.Chart().from_dict(json.load(charjson))
# chart_2= alt.Chart().from_json(json.load(Path.cwd() / 'charts' / 'ihm_corr_chart_intervals.json'))
chart_2

alt.LayerChart(...)

## Line chart for Interharmonic Intervals

In [24]:
## Ground truthc
empirical_ranking_numbered = range(0, len(empirical_ranking_intervals))

    
normalized_values_plottable = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]


df_gt = pd.DataFrame({
    'normalized_value':normalized_values_plottable,
    'chord_label':empirical_ranking_intervals
})

df_gt['method'] = 'Empirical ranking'


In [25]:
## First we need to norm values and draw a chart that draws a line for the ranking

biggest_df = pd.read_csv('overall_interharmonic_normalized_tension_scores_correlation_with_empirical_intervals.csv')

### cleaning unnecessary methods
df_chan = df_to_work_with['method'].str.contains('Chan')
df_to_work_with.method.unique()
df_exp_no_only = df_to_work_with['method'].str.contains("normed_weighted_modulations")
exception = df_to_work_with['method'].str.contains("without weights on regions")

new_df = biggest_df[(df_exp_no_only)|df_chan |exception]
new_df.method.unique()


array(["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations"],
      dtype=object)

In [26]:


## cleaning method names for better visualization
new_df['method'] = new_df['method'].str.replace("Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations","Chan's method")
new_df['method'] = new_df['method'].str.replace("and distributive Cap 0 normed_values_only_modulations","")
new_df['method'] = new_df['method'].str.replace("and distributive Cap 0 normed_values_normed_weighted_modulations","",regex=True)
new_df['method'].unique()

C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\1362872612.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['method'] = new_df['method'].str.replace("Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations","Chan's method")
C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\1362872612.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['method'] = new_df['method'].str.replace("and distributive Cap 0 normed_values_only_modulations","")
C:\Users\gabri\AppData\Local\Temp

array(["Chan's method",
       "Experimental_methods's  with weights on harmonics and weights on regions ",
       "Experimental_methods's  with weights on harmonics without weights on regions ",
       "Experimental_methods's  without weights on harmonics and weights on regions ",
       "Experimental_methods's  without weights on harmonics without weights on regions "],
      dtype=object)

In [27]:
mapping_to_new_names = {"Chan's method": "Method A",
       "Experimental_methods's  with weights on harmonics and weights on regions ":"Method E",
       "Experimental_methods's  with weights on harmonics without weights on regions ":"Method D",
       "Experimental_methods's  without weights on harmonics and weights on regions ":"Method C",
       "Experimental_methods's  without weights on harmonics without weights on regions ":"Method B"}
new_df['method'] = new_df['method'].map(mapping_to_new_names)
new_df.method.unique()

C:\Users\gabri\AppData\Local\Temp\ipykernel_31028\2230183771.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['method'] = new_df['method'].map(mapping_to_new_names)


array(['Method A', 'Method E', 'Method D', 'Method C', 'Method B'],
      dtype=object)

In [28]:

import altair as alt


## then we need to plot lines based on those values. 

line_chart = alt.Chart(new_df).mark_line(
    opacity=0.5
).encode(
    x=alt.X('harmonics_considered', title='Harmonics considered to computer Interharmonic Modulation'),
    y=alt.Y('correlation'),
    color=alt.Color('method',legend=None),
    
    
)
line_chart
## we can extract these values of correlation out of the correlation csv 

## Take the column and assign the x to each y, and plot. 

## create big dataframe for line chart

alt.Chart(...)

In [29]:
point_chart = alt.Chart(new_df).encode(
       x=alt.X('harmonics_considered', title='Harmonics considered to computer Interharmonic Modulation', scale=alt.Scale(domain=[2,32],clamp=True)),
    y=alt.Y('correlation', title='Correlation with Empirical Interval Ranking'),
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
    shape=alt.Shape('method',legend=None  ),

)
interval_line_chart_corr = (point_chart.mark_point() + point_chart.mark_line(opacity=0.5)).resolve_scale(color='shared', shape='shared')

In [30]:
interval_line_chart_corr = interval_line_chart_corr.properties(height=300,width=380,title='Correlation with interval ranking for each interharmonic method').configure_legend(labelLimit=1000,orient='bottom', direction='vertical')
interval_line_chart_corr.save(Path.cwd() / 'charts' / 'ihm_corr_line_chart_intervals.json')
interval_line_chart_corr


alt.LayerChart(...)

In [31]:
(point_chart.mark_point()+line_chart).properties(height=300,width=380,title='Correlation with interval ranking for each interharmonic method').configure_legend(labelLimit=1000,orient='bottom', direction='vertical').resolve_scale(color='independent',)

alt.LayerChart(...)

## Now consider cases

In [ ]:
# df_per_chord_label['method'].unique()

array(["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
       "Experimental_methods's  without weights on 

In [163]:
periods_considered = 12

best_ones=["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
"Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations"
       ]

## get df for each interval

df_per_chord_label = ihm.convert_correlation_df_to_a_line_chart_df(new_df,empirical_ranking_names=empirical_ranking_intervals,column_to_convert='final_ranking_correlate',group_by_methods_array=['method','harmonics_considered'])
df_per_chord_label

Normalized values for each rank: [0.0, 0.0, 0.0, 0.0, 0.0, 0.5, 0.0, 1.0, 0.0, 0.5, 1.0, 0.5, 1.0]
Normalized values for each rank: [0.0, 0.0, 0.0, 0.3333333333333333, 0.3333333333333333, 0.6666666666666666, 0.3333333333333333, 1.0, 0.3333333333333333, 0.6666666666666666, 1.0, 0.3333333333333333, 1.0]
Normalized values for each rank: [0.0, 0.0, 0.2, 0.2, 0.4, 0.6, 0.4, 1.0, 0.4, 0.6, 1.0, 0.4, 0.8]
Normalized values for each rank: [0.0, 0.0, 0.2857142857142857, 0.14285714285714285, 0.2857142857142857, 0.42857142857142855, 0.2857142857142857, 0.8571428571428571, 0.5714285714285714, 0.42857142857142855, 1.0, 0.42857142857142855, 0.8571428571428571]
Normalized values for each rank: [0.0, 0.0, 0.25, 0.375, 0.375, 0.625, 0.375, 0.875, 0.75, 0.625, 1.0, 0.5, 1.0]
Normalized values for each rank: [0.0, 0.0, 0.125, 0.25, 0.25, 0.375, 0.375, 0.875, 0.5, 0.375, 0.875, 0.25, 1.0]
Normalized values for each rank: [0.2222222222222222, 0.0, 0.2222222222222222, 0.3333333333333333, 0.4444444444444444,

chord_label  normalized_value    method  harmonics_considered
0              U          0.000000  Method A                     2
1             8v          0.000000  Method A                     2
2             P5          0.000000  Method A                     2
3             P4          0.000000  Method A                     2
4             M3          0.000000  Method A                     2
...          ...               ...       ...                   ...
2010          TT          0.759036  Method B                    32
2011          m7          0.313253  Method B                    32
2012          M2          0.963855  Method B                    32
2013          M7          0.180723  Method B                    32
2014          m2          1.000000  Method B                    32

[2015 rows x 4 columns]

In [164]:
harmonics_considered=6

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['harmonics_considered']==harmonics_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_intervals),
    y='normalized_value',
    color='method'
)
(line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='method')).properties(height=350,width=350)

alt.LayerChart(...)

best_ones

In [165]:
best_ones

["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
 "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_weighted_modulations_only",
 "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations"]

In [167]:
harmonics_considered=6

line_chart =alt.Chart(df_per_chord_label[(df_per_chord_label['harmonics_considered']==harmonics_considered)]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_intervals),
    y='normalized_value',
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
    shape=alt.Shape('method', legend=None)
)
line_charts = (line_chart.mark_line(opacity=0.6) + line_chart.mark_point())


chart_gt = alt.Chart(df_gt).encode(
   x=alt.X('chord_label',title='Chord Label in Empirical Ranking order', sort=empirical_ranking_intervals),
    y=alt.Y('normalized_value',title='Normalized Tension Value'),
).mark_line(
    color='black'
)
interval_line_chart_cases= (line_charts+chart_gt).properties(width=380,height=300, title='Normalized Tension ranking per Interval').resolve_scale(color='shared',shape='independent').configure_legend(orient='bottom',labelAlign='left', direction='horizontal',labelLimit=1000)
interval_line_chart_cases.save(Path.cwd() / 'charts' / 'ihm_cases_line_chart_intervals.json')
interval_line_chart_cases

alt.LayerChart(...)

##  Group together case by case corr chart and line chart

In [ ]:
with open(Path.cwd() / 'charts' / 'ihm_cases_line_chart_intervals.json') as charjson:

    
    dict_from_chart = json.load(charjson)
    # print(dict_from_chart)
    

    # ## try to remove config
    # dict_from_chart.pop('config', None)
    # dict_from_chart.pop('$schema', None)
    # print(dict_from_chart.keys())
    cases_intervals_chart = alt.Chart.from_dict(dict_from_chart)

with open(Path.cwd() / 'charts' / 'ihm_corr_chart_intervals.json') as charjson:
    corr_intervals_chart = alt.Chart.from_dict(json.load(charjson))

with open(Path.cwd() / 'charts' / 'ihm_corr_line_chart_intervals.json') as charjson:
    dict_from_chart = json.load(charjson)
    # dict_from_chart.pop('config', None)
    # dict_from_chart.pop('$schema', None)    
    # print(dict_from_chart.keys())
    corr_line_intervals_chart = alt.Chart.from_dict(dict_from_chart)

df = cases_intervals_chart.datasets.to_dict()
df.keys()

AttributeError: 'dict_keys' object has no attribute 'first'

In [152]:
original_df = df[list(df.keys())[0]]

org_df_pd = pd.DataFrame(original_df)
org_df_pd

chord_label  normalized_value  \
0            U             0.000   
1           8v             0.000   
2           P5             0.250   
3           P4             0.375   
4           M3             0.375   
..         ...               ...   
60          TT             0.500   
61          m7             0.000   
62          M2             0.500   
63          M7             0.250   
64          m2             1.000   

                                               method  harmonics_considered  
0                                       Chan's method                     6  
1                                       Chan's method                     6  
2                                       Chan's method                     6  
3                                       Chan's method                     6  
4                                       Chan's method                     6  
..                                                ...                   ...  
60  Experimental_methods's  without weights on har...                     6  
61  Experimental_methods's  without weights on har...                     6  
62  Experimental_methods's  without weights on har...                     6  
63  Experimental_methods's  without weights on har...                     6  
64  Experimental_methods's  without weights on har...                     6  

[65 rows x 4 columns]

In [120]:
corr_intervals_chart.properties(width=780,height=150)

alt.LayerChart(...)

In [122]:
interval_line_chart_corr.properties(width=390,height=300)

alt.LayerChart(...)

# Interharmonic Triads

In [194]:

## Triads to consider

triads=[
    # major
    ['C4', 'E4', 'G4'],
    ['C4', 'D#4','G#4'],
    ['C4', 'F4', 'A4'],
    #minor
    ['C4', 'D#4','G4'],
    ['C4', 'E4', 'A4'],
    ['C4', 'F4','G#4'],
    #Suspended
    ['C4', 'F4','G4'],
    ['C4', 'D4','G4'],
    ['C4', 'F4','A#4'],
    # Diminished,
    ['C4', 'D#4','F#4'],
    ['C4', 'D#4','A4'],
    ['C4', 'F#4','A4'],
    # augmented
    ['C4', 'E4','G#4'],
]
chord_labels_triads = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]
biggest_df = None


In [195]:

biggest_df=pipeline_for_interharmonic_normalized_tension_scores(triads, chord_labels_triads)

Now processing 2 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 3 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 4 harmonics


...

C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 31 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with em

Now processing 32 harmonics


C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:71: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  biggest_df = pd.concat([biggest_df, df_for_method], ignore_index=True)
C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\2707738574.py:97: FutureWarning: The behavior of DataFrame concatenation with em

13 chords * 18 methods * 31 harmonics

In [196]:
biggest_df

note_combination chord_label  \
0           C4,E4,G#4        CAug   
1            C4,F4,A4       FM2nd   
2            C4,E4,A4       Am1st   
3           C4,F4,A#4    Fsus42nd   
4            C4,E4,G4          CM   
...               ...         ...   
4025         C4,F4,G4       Csus4   
4026         C4,D4,G4       Csus2   
4027         C4,E4,G4          CM   
4028        C4,D#4,G4          Cm   
4029       C4,D#4,F#4        Cdim   

                             raw_values_per_combination  \
0                      [[0, 0], [0, 0], [0, 0], [0, 0]]   
1                      [[0, 0], [0, 1], [0, 0], [0, 0]]   
2                      [[0, 0], [0, 1], [0, 0], [0, 0]]   
3                      [[0, 0], [0, 1], [0, 0], [0, 0]]   
4                      [[0, 0], [0, 0], [0, 0], [0, 2]]   
...                                                 ...   
4025  [[9, 49, 55, 56, 70, 50, 62, 60, 60, 60, 59, 5...   
4026  [[15, 54, 66, 61, 63, 57, 58, 57, 61, 56, 58, ...   
4027  [[12, 51, 54, 48, 75, 62, 68, 51, 62, 57, 59, ...   
4028  [[12, 55, 52, 68, 63, 59, 63, 56, 59, 58, 59, ...   
4029  [[12, 55, 52, 68, 63, 59, 63, 56, 59, 58, 59, ...   

     weighted_modulations_per_region_in_note_combinations  \
0                                                  None     
1                                                  None     
2                                                  None     
3                                                  None     
4                                                  None     
...                                                 ...     
4025                                               None     
4026                                               None     
4027                                               None     
4028                                               None     
4029                                               None     

     weighted_sum_per_region_normalized_tension_value  \
0                                                None   
1                                                None   
2                                                None   
3                                                None   
4                                                None   
...                                               ...   
4025                                             None   
4026                                             None   
4027                                             None   
4028                                             None   
4029                                             None   

      raw_t_score_summed_only_modulations  \
0                                     0.0   
1                                     1.0   
2                                     1.0   
3                                     1.0   
4                                     2.0   
...                                   ...   
4025                               2813.0   
4026                               2813.0   
4027                               2817.0   
4028                               2817.0   
4029                               2824.0   

      raw_t_score_summed_using_weighted_normalized_value  \
0                                                   NaN    
1                                                   NaN    
2                                                   NaN    
3                                                   NaN    
4                                                   NaN    
...                                                 ...    
4025                                                NaN    
4026                                                NaN    
4027                                                NaN    
4028                                                NaN    
4029                                                NaN    

      raw_t_score_summed_using_weighted_modulations_no_norm  \
0                                                   NaN       
1                                            

In [197]:
chord_labels_triads           = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads      = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]

new_df_with_explicit_ratings  = break_into_different_rankings(biggest_df,empirical_ranking=empirical_ranking_triads,numbered_ranking=empirical_ranking_nums_triads, method_column='method',x_axis='harmonics_considered', normed_values_columns=normed_values_columns)

In [198]:
new_df_with_explicit_ratings = new_df_with_explicit_ratings.dropna()
new_df_with_explicit_ratings.to_csv('overall_interharmonic_normalized_tension_scores_correlation_with_explicit_empirical_triads.csv', index=False)

## Reading interharmonic triads correlation

In [236]:
chord_labels_triads           = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads      = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]

new_df_with_explicit_ratings = pd.read_csv('overall_interharmonic_normalized_tension_scores_correlation_with_explicit_empirical_triads.csv')

In [237]:

### cleaning unnecessary methods
df_chan = new_df_with_explicit_ratings['method'].str.contains('Chan')
new_df_with_explicit_ratings.method.unique()
df_exp_no_only = new_df_with_explicit_ratings['method'].str.contains("normed_weighted_modulations")
exception = new_df_with_explicit_ratings['method'].str.contains("without weights on regions")

new_df = new_df_with_explicit_ratings[(df_exp_no_only)|df_chan |exception]
new_df.method.unique()


array(["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Chan's method Vanilla Cap 0 with  non-distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions

### Distributive  change

In [239]:
## First graph should be distributive vs non-distributive
methods_not_distributive = new_df['method'].str.contains('non-distributive')

new_df['distributive'] = ~methods_not_distributive 

new_df[new_df['distributive'] == True]['method'].unique()

C:\Users\gabri\AppData\Local\Temp\ipykernel_37240\3215327275.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  new_df['distributive'] = ~methods_not_distributive


array(["Chan's method Vanilla Cap 0 with  distributive normed_values_only_modulations",
       "Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
       "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_normed_weighted_modulations",
       "Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations"],
      dtype=object)

In [243]:
mapping_to_new_names = {"Chan's method": "Method A",
       "Experimental_methods's  with weights on harmonics and weights on regions ":"Method E",
       "Experimental_methods's  with weights on harmonics without weights on regions ":"Method D",
       "Experimental_methods's  without weights on harmonics and weights on regions ":"Method C",
       "Experimental_methods's  without weights on harmonics without weights on regions ":"Method B"}

new_mapping = {
    "distributive":{},
    "non-distributive":{}
}

## creating new maps,
for key in mapping_to_new_names.keys():

    new_mapping["distributive"][new_df[new_df['method'].str.contains(key) & (new_df['distributive']==True)]['method'].unique()[0]] = ""
    new_mapping["non-distributive"][new_df[new_df['method'].str.contains(key) & (new_df['distributive']==False)]['method'].unique()[0]] = ""



## convert to simpler names, Chan to Method A, and follow mapping to new name order
for ((key,val),(new_df_key,new_df_val),(non_dist_key,non_dist_val)) in zip(mapping_to_new_names.items(),new_mapping["distributive"].items(),new_mapping["non-distributive"].items()):
    new_mapping["distributive"][new_df_key]=val #+ " - distributive"
    new_mapping["non-distributive"][non_dist_key]=val #+ " - non-distributive"

new_mapping
new_df[new_df['method'].str.contains('without weights on harmonics without weights on regions')]

method  harmonics_considered  \
248  Experimental_methods's  without weights on har...                     2   
249  Experimental_methods's  without weights on har...                     3   
250  Experimental_methods's  without weights on har...                     4   
251  Experimental_methods's  without weights on har...                     5   
252  Experimental_methods's  without weights on har...                     6   
..                                                 ...                   ...   
553  Experimental_methods's  without weights on har...                    28   
554  Experimental_methods's  without weights on har...                    29   
555  Experimental_methods's  without weights on har...                    30   
556  Experimental_methods's  without weights on har...                    31   
557  Experimental_methods's  without weights on har...                    32   

                      normed_column  correlation   p_value  \
248  normed_values_only_modulations    -0.025652  0.933705   
249  normed_values_only_modulations     0.516008  0.071054   
250  normed_values_only_modulations     0.458698  0.114895   
251  normed_values_only_modulations     0.384961  0.193978   
252  normed_values_only_modulations     0.526056  0.064804   
..                              ...          ...       ...   
553  normed_values_only_modulations    -0.035561  0.908183   
554  normed_values_only_modulations    -0.067579  0.826371   
555  normed_values_only_modulations    -0.080172  0.794588   
556  normed_values_only_modulations    -0.079130  0.797210   
557  normed_values_only_modulations    -0.071058  0.817565   

                               final_ranking_correlate  distributive  
248  [1.0, 1.0, 0.0, 0.0, 1.0, 1.0, 1.0, 1.0, 0.0, ...          True  
249  [0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 1.0, 0.0, ...          True  
250  [0.5, 0.5, 0.25, 0.0, 0.5, 0.25, 0.25, 0.5, 0....          True  
251  [0.5, 0.5, 0.0, 0.0, 0.75, 0.25, 0.25, 0.75, 0...          True  
252  [0.2, 0.2, 0.0, 0.0, 0.6, 0.2, 0.2, 0.6, 0.0, ...          True  
..                                                 ...           ...  
553  [0.8611111111111112, 0.8611111111111112, 0.305...         False  
554  [0.825, 0.825, 0.225, 0.0, 0.625, 0.75, 0.75, ...         False  
555  [0.8095238095238095, 0.8095238095238095, 0.214...         False  
556  [0.8409090909090909, 0.8409090909090909, 0.25,...         False  
557  [0.86, 0.86, 0.28, 0.0, 0.6, 0.78, 0.78, 0.6, ...         False  

[62 rows x 7 columns]

In [ ]:


new_df['method']= new_df.apply(lambda row: new_mapping["distributive"][row['method']] if row['distributive'] == True else new_mapping["non-distributive"][row['method']], axis=1)
new_df.method.unique()


In [234]:
distributive_df = new_df[new_df['distributive'] == True]
non_distributive_df = new_df[new_df['distributive'] == False]


In [235]:
alt.Chart(distributive_df).mark_boxplot().encode(
    x=alt.X('method'),
    y=alt.Y('correlation'),
    color=alt.Color('method')
    
) | alt.Chart(non_distributive_df).mark_boxplot().encode(
    x=alt.X('method'),
    y=alt.Y('correlation'),
    color=alt.Color('method')
    
)


alt.HConcatChart(...)

## Interharmonic Triads correlation chart

In [244]:
corr_chart,text_chart = ihm.create_corr_heatmap(new_df_with_explicit_ratings, x='harmonics_considered', y='method',  p_value_column='p_value', corr_column='correlation')

interval_chart = (corr_chart+text_chart).properties(width=1150, height=500,title='Correlation between Empirical and Computed tension rankings for Triads')
interval_chart

alt.LayerChart(...)

## Without using explicit ratings

In [29]:

new_df_without_explicit_ratings = break_into_different_rankings(biggest_df,empirical_ranking=empirical_ranking_triads,numbered_ranking=None, method_column='method',x_axis='harmonics_considered', normed_values_columns=normed_values_columns)

NameError: name 'break_into_different_rankings' is not defined

In [30]:
new_df_without_explicit_ratings = new_df_without_explicit_ratings.dropna()
new_df_without_explicit_ratings.to_csv('overall_interharmonic_normalized_tension_scores_correlation_with_no_unexplicit_empirical_triads.csv', index=False)


NameError: name 'new_df_without_explicit_ratings' is not defined

In [34]:
new_df_without_explicit_ratings = pd.read_csv('overall_interharmonic_normalized_tension_scores_correlation_with_no_unexplicit_empirical_triads.csv')

## without using explicit ratings corr df

In [36]:

corr_chart,text_chart = ihm.create_corr_heatmap(new_df_without_explicit_ratings, x='harmonics_considered', y='method',  p_value_column='p_value', corr_column='correlation')

interval_chart = (corr_chart+text_chart).properties(width=1200, height=400,title='Correlation between Empirical and Computed tension rankings for Triads')
interval_chart

alt.LayerChart(...)

## Line chart for interharmonic triads

In [37]:
## Ground truthc
empirical_ranking_numbered = range(0, len(empirical_ranking_triads))

    
normalized_values_plottable_without_explicit = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]

normalized_values_num_ranked= [(x - min(empirical_ranking_nums_triads)) / (max(empirical_ranking_nums_triads) - min(empirical_ranking_nums_triads)) for x in empirical_ranking_nums_triads]


df_gt = pd.DataFrame({
    'normalized_value_rank_num':normalized_values_num_ranked,
    'chord_label':empirical_ranking_triads,
    'normalized_value':normalized_values_plottable_without_explicit
})

df_gt['method'] = 'Empirical ranking'


In [38]:
## First we need to norm values and draw a chart that draws a line for the ranking

biggest_df = pd.read_csv('overall_interharmonic_normalized_tension_scores_correlation_with_explicit_empirical_triads.csv')

## eliminating all that have normed_values_only_modulations

method_not_allowed = [] 
for unique_method in biggest_df.method.unique():
    if 'Experiment' in unique_method and 'normed_values_only_modulations' in unique_method:
        method_not_allowed.append(unique_method)
        
method_not_allowed

["Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics without weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmo

In [39]:

## eliminating all that have normed_values_only_modulations

method_not_allowed = [] 
for unique_method in biggest_df.method.unique():
    if 'Experiment' in unique_method and 'normed_values_only_modulations' in unique_method:
        method_not_allowed.append(unique_method)
        
method_not_allowed

["Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics without weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmo

In [40]:


biggest_df =biggest_df[~biggest_df.method.isin(method_not_allowed)]

In [41]:

import altair as alt


## then we need to plot lines based on those values. 

line_chart = alt.Chart(biggest_df).mark_line(
    opacity=0.5
).encode(
    x=alt.X('harmonics_considered', title='Harmonics considered to computer Interharmonic Modulation'),
    y=alt.Y('correlation'),
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
    
)
line_chart
## we can extract these values of correlation out of the correlation csv 

## Take the column and assign the x to each y, and plot. 

## create big dataframe for line chart

alt.Chart(...)

In [42]:
point_chart = alt.Chart(biggest_df).encode(
       x=alt.X('harmonics_considered', title='Harmonics considered to computer Interharmonic Modulation'),
    y=alt.Y('correlation'),
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
    shape=alt.Shape('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),

)
point_chart.mark_point()

alt.Chart(...)

In [44]:
(point_chart.mark_point()+line_chart).properties(height=400,width=400,title='Correlation with triads numeric ranking for each interharmonic method').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')

alt.LayerChart(...)

In [49]:
periods_considered = 12



## get df for each interval

df_per_chord_label = ihm.convert_correlation_df_to_a_line_chart_df(biggest_df,empirical_ranking_names=empirical_ranking_triads,column_to_convert='final_ranking_correlate',group_by_methods_array=['method','harmonics_considered'])
df_per_chord_label

Normalized values for each rank: [0.5, 0.5, 0.25, 0.25, 0.5, 0.5, 0.5, 0.5, 0.75, 0.25, 0.75, 1.0, 0.0]
Normalized values for each rank: [0.25, 0.25, 0.25, 0.25, 0.5, 0.25, 0.25, 0.5, 0.75, 0.25, 0.75, 1.0, 0.0]
Normalized values for each rank: [0.42857142857142855, 0.42857142857142855, 0.14285714285714285, 0.0, 0.42857142857142855, 0.2857142857142857, 0.2857142857142857, 0.42857142857142855, 0.7142857142857143, 0.14285714285714285, 0.7142857142857143, 1.0, 0.14285714285714285]
Normalized values for each rank: [0.45454545454545453, 0.45454545454545453, 0.09090909090909091, 0.0, 0.36363636363636365, 0.45454545454545453, 0.45454545454545453, 0.36363636363636365, 0.7272727272727273, 0.09090909090909091, 0.7272727272727273, 1.0, 0.09090909090909091]
Normalized values for each rank: [0.2727272727272727, 0.2727272727272727, 0.18181818181818182, 0.18181818181818182, 0.36363636363636365, 0.36363636363636365, 0.36363636363636365, 0.36363636363636365, 0.8181818181818182, 0.18181818181818182, 0.8

chord_label  normalized_value  \
0             CM          0.500000   
1             Cm          0.500000   
2          FM2nd          0.250000   
3       Fsus42nd          0.250000   
4         G#M1st          0.500000   
...          ...               ...   
4025     Adim1st          0.428362   
4026       Am1st          0.163649   
4027    F#dim2nd          0.428362   
4028        Cdim          1.000000   
4029        CAug          0.411646   

                                                 method  harmonics_considered  
0     Chan's method Vanilla Cap 0 with  distributive...                     2  
1     Chan's method Vanilla Cap 0 with  distributive...                     2  
2     Chan's method Vanilla Cap 0 with  distributive...                     2  
3     Chan's method Vanilla Cap 0 with  distributive...                     2  
4     Chan's method Vanilla Cap 0 with  distributive...                     2  
...                                                 ...                   ...  
4025  Experimental_methods's  without weights on har...                    32  
4026  Experimental_methods's  without weights on har...                    32  
4027  Experimental_methods's  without weights on har...                    32  
4028  Experimental_methods's  without weights on har...                    32  
4029  Experimental_methods's  without weights on har...                    32  

[4030 rows x 4 columns]

In [50]:
harmonics_considered=18

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['harmonics_considered']==harmonics_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
(line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='method')).properties(height=600,width=600)

alt.LayerChart(...)

In [51]:
harmonics_considered=18

line_chart =alt.Chart(df_per_chord_label[(df_per_chord_label['harmonics_considered']==harmonics_considered) & ~(df_per_chord_label['method'].isin(method_not_allowed))]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
line_charts = (line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='method'))


chart_gt = alt.Chart(df_gt).encode(
   x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value_rank_num',
).mark_line(
    color='black'
)
(line_charts+chart_gt).properties(width=350,height=350,title='Overall interharmonic tension ratings for triads ranked').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')


alt.LayerChart(...)

## without explicit

In [52]:
## Ground truthc
empirical_ranking_numbered = range(0, len(empirical_ranking_triads))

    
normalized_values_plottable_without_explicit = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]

normalized_values_num_ranked= [(x - min(empirical_ranking_nums_triads)) / (max(empirical_ranking_nums_triads) - min(empirical_ranking_nums_triads)) for x in empirical_ranking_nums_triads]


df_gt = pd.DataFrame({
    'normalized_value_rank_num':normalized_values_num_ranked,
    'chord_label':empirical_ranking_triads,
    'normalized_value':normalized_values_plottable_without_explicit
})

df_gt['method'] = 'Empirical ranking'


In [53]:
## First we need to norm values and draw a chart that draws a line for the ranking

biggest_df = pd.read_csv('overall_interharmonic_normalized_tension_scores_correlation_with_no_unexplicit_empirical_triads.csv')

## eliminating all that have normed_values_only_modulations

method_not_allowed = [] 
for unique_method in biggest_df.method.unique():
    if 'Experiment' in unique_method and 'normed_values_only_modulations' in unique_method:
        method_not_allowed.append(unique_method)
        
method_not_allowed

["Experimental_methods's  with weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics without weights on regions and distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  with weights on harmonics without weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmonics and weights on regions and non-distributive Cap 0 normed_values_only_modulations",
 "Experimental_methods's  without weights on harmo

In [54]:


biggest_df =biggest_df[~biggest_df.method.isin(method_not_allowed)]

In [55]:

import altair as alt


## then we need to plot lines based on those values. 

line_chart = alt.Chart(biggest_df).mark_line(
    opacity=0.5
).encode(
    x=alt.X('harmonics_considered', title='Harmonics considered to computer Interharmonic Modulation'),
    y=alt.Y('correlation'),
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
    
)
line_chart
## we can extract these values of correlation out of the correlation csv 

## Take the column and assign the x to each y, and plot. 

## create big dataframe for line chart

alt.Chart(...)

In [56]:
point_chart = alt.Chart(biggest_df).encode(
       x=alt.X('harmonics_considered', title='Harmonics considered to computer Interharmonic Modulation'),
    y=alt.Y('correlation', scale=alt.Scale()),
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
    shape=alt.Shape('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),

)
point_chart.mark_point()

alt.Chart(...)

In [57]:
(point_chart.mark_point()+line_chart).properties(height=300,width=300,title='Correlation with interval ranking for each method').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')

alt.LayerChart(...)

In [92]:
periods_considered = 12



## get df for each interval

df_per_chord_label = ihm.convert_correlation_df_to_a_line_chart_df(biggest_df,empirical_ranking_names=empirical_ranking_triads,column_to_convert='final_ranking_correlate',group_by_methods_array=['method','harmonics_considered'])
df_per_chord_label

Normalized values for each rank: [0.5, 0.5, 0.25, 0.25, 0.5, 0.5, 0.5, 0.5, 0.75, 0.25, 0.75, 1.0, 0.0]
Normalized values for each rank: [0.25, 0.25, 0.25, 0.25, 0.5, 0.25, 0.25, 0.5, 0.75, 0.25, 0.75, 1.0, 0.0]
Normalized values for each rank: [0.42857142857142855, 0.42857142857142855, 0.14285714285714285, 0.0, 0.42857142857142855, 0.2857142857142857, 0.2857142857142857, 0.42857142857142855, 0.7142857142857143, 0.14285714285714285, 0.7142857142857143, 1.0, 0.14285714285714285]
Normalized values for each rank: [0.45454545454545453, 0.45454545454545453, 0.09090909090909091, 0.0, 0.36363636363636365, 0.45454545454545453, 0.45454545454545453, 0.36363636363636365, 0.7272727272727273, 0.09090909090909091, 0.7272727272727273, 1.0, 0.09090909090909091]
Normalized values for each rank: [0.2727272727272727, 0.2727272727272727, 0.18181818181818182, 0.18181818181818182, 0.36363636363636365, 0.36363636363636365, 0.36363636363636365, 0.36363636363636365, 0.8181818181818182, 0.18181818181818182, 0.8

chord_label  normalized_value  \
0             CM          0.500000   
1             Cm          0.500000   
2          FM2nd          0.250000   
3       Fsus42nd          0.250000   
4         G#M1st          0.500000   
...          ...               ...   
4025     Adim1st          0.428362   
4026       Am1st          0.163649   
4027    F#dim2nd          0.428362   
4028        Cdim          1.000000   
4029        CAug          0.411646   

                                                 method  harmonics_considered  
0     Chan's method Vanilla Cap 0 with  distributive...                     2  
1     Chan's method Vanilla Cap 0 with  distributive...                     2  
2     Chan's method Vanilla Cap 0 with  distributive...                     2  
3     Chan's method Vanilla Cap 0 with  distributive...                     2  
4     Chan's method Vanilla Cap 0 with  distributive...                     2  
...                                                 ...                   ...  
4025  Experimental_methods's  without weights on har...                    32  
4026  Experimental_methods's  without weights on har...                    32  
4027  Experimental_methods's  without weights on har...                    32  
4028  Experimental_methods's  without weights on har...                    32  
4029  Experimental_methods's  without weights on har...                    32  

[4030 rows x 4 columns]

In [58]:
harmonics_considered=18

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['harmonics_considered']==harmonics_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
(line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='method')).properties(height=600,width=600)

alt.LayerChart(...)

In [61]:
harmonics_considered=18

line_chart =alt.Chart(df_per_chord_label[(df_per_chord_label['harmonics_considered']==harmonics_considered) & ~(df_per_chord_label['method'].isin(method_not_allowed))]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
line_charts = (line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='method'))


chart_gt = alt.Chart(df_gt).encode(
   x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
).mark_line(
    color='black'
)
(line_charts+chart_gt).properties(width=350,height=350,title='Overall interharmonic tension ratings for triads ranked').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')


alt.LayerChart(...)

# Subharmonic tension intervals

Here we divide three to four parts. Due to equation21 having a denominator with very small numbers, and their figure says as it approximates 0 return 0, we then need to  consider, which 10**(-exp) we need to use.
 - We are going to compute for 32 periods different correlations for each period for each threshold. 
- Then we average the correlations to choose best performing threshold on average

In [1]:
import psychoacoustic_tension_chan_module.subharmonic_module as shm
import pandas as pd


In [25]:

## Do intervals!

notes = ['G2','G#2','A2','A#2','B2','C3','C#3','D3','D#3','E3','F3','F#3','G3']

## generating intervals
intervals = []
for note in notes:
    intervals.append(['G2',note])

chord_labels_intervals = ['U', 'm2', 'M2', 'm3', 'M3', 'P4', 'TT', 'P5', 'm6', 'M6', 'm7', 'M7', '8v']

empirical_ranking_intervals = ['U','8v','P5','P4','M3','M6','m6','m3','TT','m7','M2','M7','m2']


## Triads to consider

triads=[
    # major
    ['C4', 'E4', 'G4'],
    ['C4', 'D#4','G#4'],
    ['C4', 'F4', 'A4'],
    #minor
    ['C4', 'D#4','G4'],
    ['C4', 'E4', 'A4'],
    ['C4', 'F4','G#4'],
    #Suspended
    ['C4', 'F4','G4'],
    ['C4', 'D4','G4'],
    ['C4', 'F4','A#4'],
    # Diminished,
    ['C4', 'D#4','F#4'],
    ['C4', 'D#4','A4'],
    ['C4', 'F#4','A4'],
    # augmented
    ['C4', 'E4','G#4'],
]
chord_labels_triads = ['CM', 'G#M1st', 'FM2nd', 'Cm', 'Am1st', 'Fm2nd', 'Csus4','Csus2', 'Fsus42nd', 'Cdim','Adim1st', 'F#dim2nd', 'CAug']
empirical_ranking_triads = ['CM', 'Cm', 'FM2nd', 'Fsus42nd', 'G#M1st','Csus2','Csus4', 'Fm2nd','Adim1st','Am1st', 'F#dim2nd','Cdim', 'CAug' ]
empirical_ranking_nums_triads = [1.667,2.407,2.741,2.852,2.889,3.111,3.148,3.481,3.519,3.593,3.667,3.889,5.259]


periods_considered = [4,5,6,7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32]
threshold_exponents = [1,2,3,4,5,6,7,8,9,10,11,12]

In [31]:



def pipeline_for_subharmonic_normalized_tension_score(notes_to_consider, chord_labels,periods_considered, threshold_exponent_to_apply=3):

    ## we define periods to  consider



    subharmonic_per_period = pd.DataFrame()

    for p in periods_considered:
        all_notes_subharmonic_tension = shm.compute_subharmonic_tension_for_each_note_array(notes_to_consider,chord_labels,periods_considered=p,threshold_neg_exp_for_equation_21=threshold_exponent_to_apply)
        all_notes_subharmonic_tension = shm.compute_normalized_subharmonic_tension_for_each_case(all_notes_subharmonic_tension)

        all_notes_subharmonic_tension['periods_considered']=p
        
        # print(all_notes_subharmonic_tension)

        subharmonic_per_period = pd.concat([subharmonic_per_period,all_notes_subharmonic_tension],ignore_index=False)
    return subharmonic_per_period


        

## Now compute for each threshold considered

In [32]:
def pipeline_for_threshold_considered(notes_to_consider,chord_labels,threshold_exponents,periods_considered):
    subharmonic_per_threshold = pd.DataFrame()

    for threshold in threshold_exponents:
        print(f'Now processing threshold exponent {threshold}')
        
        df_for_threshold = pipeline_for_subharmonic_normalized_tension_score(notes_to_consider=notes_to_consider,chord_labels=chord_labels,periods_considered=periods_considered,threshold_exponent_to_apply=threshold)
        df_for_threshold['threshold_exponent'] = "10**" + str(threshold)

        subharmonic_per_threshold = pd.concat([subharmonic_per_threshold,df_for_threshold],ignore_index=False)
    return subharmonic_per_threshold        
    

In [33]:
interval_subharmonic_w_threshholds = pipeline_for_threshold_considered(notes_to_consider=intervals,chord_labels=chord_labels_intervals,threshold_exponents=threshold_exponents,periods_considered=periods_considered)
interval_subharmonic_w_threshholds

Now processing threshold exponent 1
Now processing threshold exponent 2
Now processing threshold exponent 3
Now processing threshold exponent 4
Now processing threshold exponent 5
Now processing threshold exponent 6
Now processing threshold exponent 7
Now processing threshold exponent 8
Now processing threshold exponent 9
Now processing threshold exponent 10
Now processing threshold exponent 11
Now processing threshold exponent 12


t_values  mean_t_sub      indices  \
0    [0.010204200439176117, 0.010204200439176117]    0.010204   [0.0, 0.0]   
1    [0.010204200439176117, 0.020408400878352235]    0.015306   [0.0, 1.0]   
2    [0.020408400878352235, 0.020408400878352235]    0.020408   [1.0, 1.0]   
3    [0.010204200439176117, 0.010204200439176117]    0.010204   [0.0, 0.0]   
4    [0.020408400878352235, 0.020408400878352235]    0.020408   [1.0, 1.0]   
..                                            ...         ...          ...   
229   [0.06122520263505671, 0.061225202635056715]    0.061225  [5.0, 11.0]   
230    [0.09183780395258506, 0.09183780395258508]    0.091838  [8.0, 17.0]   
231  [0.030612601317528354, 0.030612601317528357]    0.030613   [2.0, 5.0]   
232   [0.06122520263505671, 0.061225202635056715]    0.061225  [5.0, 11.0]   
233    [0.09183780395258506, 0.09183780395258508]    0.091838  [8.0, 17.0]   

     difference_(delta_t)  difference_ratio_(delta_t_hat)  \
0            0.000000e+00                    0.000000e+00   
1            1.020420e-02                    6.666667e-01   
2            0.000000e+00                    0.000000e+00   
3            0.000000e+00                    0.000000e+00   
4            0.000000e+00                    0.000000e+00   
..                    ...                             ...   
229          6.938894e-18                    1.133339e-16   
230          1.387779e-17                    1.511119e-16   
231          3.469447e-18                    1.133339e-16   
232          6.938894e-18                    1.133339e-16   
233          1.387779e-17                    1.511119e-16   

                                                  case  tension_score  \
0              Smallest_t_sub_and_choose_top_3_delta_t            0.0   
1              Smallest_t_sub_and_choose_top_3_delta_t            0.0   
2              Smallest_t_sub_and_choose_top_3_delta_t            0.0   
3              Smallest_delta_t_and_choose_top_3_t_sub            0.0   
4              Smallest_delta_t_and_choose_top_3_t_sub            0.0   
..                                                 ...            ...   
229        Smallest_ratio_and_filter_by_smallest_t_sub            0.0   
230        Smallest_ratio_and_filter_by_smallest_t_sub            0.0   
231  Smallest_ratio_and_filter_by_smallest_t_sub_wi...            0.0   
232  Smallest_ratio_and_filter_by_smallest_t_sub_wi...            0.0   
233  Smallest_ratio_and_filter_by_smallest_t_sub_wi...            0.0   

    note_names chord_label  normalized_tension_score  periods_considered  \
0        G2,G2           U                       0.0                   4   
1        G2,G2           U                       0.0                   4   
2        G2,G2           U                       0.0                   4   
3        G2,G2           U                       0.0                   4   
4        G2,G2           U                       0.0                   4   
..         ...         ...                       ...                 ...   
229      G2,G3          8v                       0.0                  32   
230      G2,G3          8v                       0.0                  32   
231      G2,G3          8v                       0.0                  32   
232      G2,G3          8v                       0.0                  32   
233      G2,G3          8v                       0.0                  32   

    threshold_exponent  
0                10**1  
1                10**1  
2                10**1  
3                10**1  
4                10**1  
..                 ...  
229             10**12  
230             10**12  
231             10**12  
232             10**12  
233             10**12  

[81432 rows x 12 columns]

NOw we have a particular df, that contains the top_n elements from equation 21, for each case for each notes. So if top_n is 3 then we have for each note we have 6* 3 cases, 6 * 3 tension scores, 6 * 3 normalized_tension score. 

So we have to group each case and notes. Then each case will contain every note, and tension scores. 

In [34]:
## first clean the top_m things

grouped_df = interval_subharmonic_w_threshholds.drop(['t_values','mean_t_sub','indices', 'difference_(delta_t)', 'difference_ratio_(delta_t_hat)'], axis=1)
grouped_df = grouped_df.groupby(['case','note_names','periods_considered','threshold_exponent']).first().reset_index()
grouped_df

case note_names  \
0            Smallest_delta_t_and_choose_top_3_t_sub     G2,A#2   
1            Smallest_delta_t_and_choose_top_3_t_sub     G2,A#2   
2            Smallest_delta_t_and_choose_top_3_t_sub     G2,A#2   
3            Smallest_delta_t_and_choose_top_3_t_sub     G2,A#2   
4            Smallest_delta_t_and_choose_top_3_t_sub     G2,A#2   
...                                              ...        ...   
27139  Smallest_t_sub_and_filter_by_smallest_delta_t      G2,G3   
27140  Smallest_t_sub_and_filter_by_smallest_delta_t      G2,G3   
27141  Smallest_t_sub_and_filter_by_smallest_delta_t      G2,G3   
27142  Smallest_t_sub_and_filter_by_smallest_delta_t      G2,G3   
27143  Smallest_t_sub_and_filter_by_smallest_delta_t      G2,G3   

       periods_considered threshold_exponent  tension_score chord_label  \
0                       4              10**1       0.000000          m3   
1                       4             10**10    9019.475174          m3   
2                       4             10**11    9019.475174          m3   
3                       4             10**12    9019.475174          m3   
4                       4              10**2       0.000000          m3   
...                   ...                ...            ...         ...   
27139                  32              10**5    7478.394594          8v   
27140                  32              10**6    7478.394594          8v   
27141                  32              10**7    7478.394594          8v   
27142                  32              10**8    7478.394594          8v   
27143                  32              10**9    7478.394594          8v   

       normalized_tension_score  
0                      0.000000  
1                      0.158009  
2                      0.158009  
3                      0.158009  
4                      0.000000  
...                         ...  
27139                  0.131012  
27140                  0.131012  
27141                  0.131012  
27142                  0.131012  
27143                  0.131012  

[27144 rows x 7 columns]

In [35]:
## now save csv with scores

grouped_df.to_csv('overall_subharmonic_tension_intervals_with_tension_score_normalized_per_period_per_threshold.csv')

## linechart of average correlation per threshold

After computing all possible thresholds and tension scores, we should now average each correlationand plot a linechart, to see, for each case (color) what is the average correlation (y axis) given threshold (x axis)

### Now we are going to create a correlation df

In [36]:
new_df = pd.DataFrame()

def create_corr_df_for_subharmonic_periods_cases(subharmonic_df, 
                                   empirical_ranking=[],
                                   empirical_ranking_num=None,
                                   labels_to_compare_with_rank='chord_labels', 
                                   column_to_compare_with_rank='normalized_tension_score',
                                   break_into_methods='case',
                                   periods='periods_considered'):
    
    ## we create a correlation df using the empirical ranking and the subharmonic df provided
    ## this function creates a correlation dataframe using the rank for a period and a case
    

    for_all_corr_df = pd.DataFrame()

    ## now divide for each period
    for p_case in subharmonic_df[periods].unique():
        period_df = subharmonic_df[subharmonic_df[periods]==p_case]
        # print(period_df.shape)

        ## after period divide for each case
        for method in period_df[break_into_methods].unique():
            methods_in_period_df = period_df[period_df[break_into_methods]==method]

            correlation, p_value, scores_for_each_chord_based_on_emp = shm.get_correlation_between_empirical_and_method(empirical_ranking=empirical_ranking,
                                                                                                                    df_with_rankings=methods_in_period_df,
                                                                                                                    numbered_ranking=empirical_ranking_num,
                                                                                                                    chord_label_column=labels_to_compare_with_rank,
                                                                                                                    column_to_compare_with_emp=column_to_compare_with_rank)
            smaller_corr_df = pd.DataFrame({
                'correlation':[correlation],
                'scores_based_on_emp_rank':[scores_for_each_chord_based_on_emp],
                'p_value':[p_value],
                'subharmonic_method':[method],
                'periods_considered':[p_case],
    
            })

            # print(smaller_corr_df)
            # return
            for_all_corr_df = pd.concat([for_all_corr_df,smaller_corr_df], ignore_index=True)

    return for_all_corr_df

            

### We now have corr df per case per period, we need to do per threshold as well

In [37]:
def create_corr_df_for_subharmonic_per_threshold(subharmonic_df, 
                                   empirical_ranking=[],
                                   empirical_ranking_num=None,
                                   labels_to_compare_with_rank='chord_labels', 
                                   column_to_compare_with_rank='normalized_tension_score',
                                   break_into_methods='case',
                                   periods='periods_considered',
                                   threshold_column='threshold_exponent'):
    all_corr_df = pd.DataFrame()

    for threshold in subharmonic_df[threshold_column].unique():
        print(f'Now processing threshold {threshold}')


        threshold_df = subharmonic_df[subharmonic_df[threshold_column]==threshold]

        corr_df_for_threshold = create_corr_df_for_subharmonic_periods_cases(subharmonic_df=threshold_df,
                                                                             empirical_ranking=empirical_ranking,
                                                                             empirical_ranking_num=empirical_ranking_num,
                                                                             labels_to_compare_with_rank=labels_to_compare_with_rank,
                                                                             column_to_compare_with_rank=column_to_compare_with_rank,
                                                                             break_into_methods=break_into_methods,
                                                                             periods=periods)
        corr_df_for_threshold['threshold_exponent'] = threshold

        all_corr_df = pd.concat([all_corr_df,corr_df_for_threshold], ignore_index=True)
    return all_corr_df

In [38]:
interval_corr_df_w_thresh_period_case = create_corr_df_for_subharmonic_per_threshold(grouped_df,empirical_ranking=empirical_ranking_intervals,empirical_ranking_num=None, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')

Now processing threshold 10**1


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**10
Now processing threshold 10**11
Now processing threshold 10**12
Now processing threshold 10**2


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**3


...

Now processing threshold 10**4


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**5


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**6
Now processing threshold 10**7
Now processing threshold 10**8
Now processing threshold 10**9


In [39]:
interval_corr_df_w_thresh_period_case

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
2083    -0.391206  [0.0, 0.0, 1.0, 0.6546922875876561, 0.01263436...   
2084    -0.378209  [0.0, 0.0, 1.0, 0.6546922875876561, 0.01110522...   
2085    -0.254623  [0.0, 0.0, 1.0, 0.8091305751160662, 0.10538133...   
2086    -0.017090  [0.30182007841980996, 0.0, 0.7214823642898025,...   
2087     0.616830  [0.0, 0.1310116144078594, 0.08697656346378536,...   

       p_value                                 subharmonic_method  \
0          NaN            Smallest_delta_t_and_choose_top_3_t_sub   
1          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2          NaN        Smallest_ratio_and_filter_by_smallest_t_sub   
3          NaN  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
4          NaN            Smallest_t_sub_and_choose_top_3_delta_t   
...        ...                                                ...   
2083  0.186228  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2084  0.202582        Smallest_ratio_and_filter_by_smallest_t_sub   
2085  0.401177  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
2086  0.955809            Smallest_t_sub_and_choose_top_3_delta_t   
2087  0.024731      Smallest_t_sub_and_filter_by_smallest_delta_t   

      periods_considered threshold_exponent  
0                      4              10**1  
1                      4              10**1  
2                      4              10**1  
3                      4              10**1  
4                      4              10**1  
...                  ...                ...  
2083                  32              10**9  
2084                  32              10**9  
2085                  32              10**9  
2086                  32              10**9  
2087                  32              10**9  

[2088 rows x 6 columns]

In [40]:
interval_corr_df_w_thresh_period_case.to_csv('subharmonic_correlation_intervals_for_thresholds_period_case.csv')

In [123]:
interval_corr_df_w_thresh_period_case = pd.read_csv('subharmonic_correlation_intervals_for_thresholds_period_case.csv')
interval_corr_df_w_thresh_period_case.drop(columns=['Unnamed: 0'], inplace=True)
# interval_corr_df_w_thresh_period_case.dropna(inplace=True)
interval_corr_df_w_thresh_period_case

correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
2083    -0.391206  [0.0, 0.0, 1.0, 0.6546922875876561, 0.01263436...   
2084    -0.378209  [0.0, 0.0, 1.0, 0.6546922875876561, 0.01110522...   
2085    -0.254623  [0.0, 0.0, 1.0, 0.8091305751160662, 0.10538133...   
2086    -0.017090  [0.30182007841980996, 0.0, 0.7214823642898025,...   
2087     0.616830  [0.0, 0.1310116144078594, 0.08697656346378536,...   

       p_value                                 subharmonic_method  \
0          NaN            Smallest_delta_t_and_choose_top_3_t_sub   
1          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2          NaN        Smallest_ratio_and_filter_by_smallest_t_sub   
3          NaN  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
4          NaN            Smallest_t_sub_and_choose_top_3_delta_t   
...        ...                                                ...   
2083  0.186228  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2084  0.202582        Smallest_ratio_and_filter_by_smallest_t_sub   
2085  0.401177  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
2086  0.955809            Smallest_t_sub_and_choose_top_3_delta_t   
2087  0.024731      Smallest_t_sub_and_filter_by_smallest_delta_t   

      periods_considered threshold_exponent  
0                      4              10**1  
1                      4              10**1  
2                      4              10**1  
3                      4              10**1  
4                      4              10**1  
...                  ...                ...  
2083                  32              10**9  
2084                  32              10**9  
2085                  32              10**9  
2086                  32              10**9  
2087                  32              10**9  

[2088 rows x 6 columns]

### Now we need to average correlation for each threshold

In [124]:
grouped_df_for_correlation = interval_corr_df_w_thresh_period_case.groupby(['subharmonic_method','threshold_exponent'])
grouped_df_for_correlation.mean(numeric_only=True).reset_index()

subharmonic_method threshold_exponent  \
0         Smallest_delta_t_and_choose_top_3_t_sub              10**1   
1         Smallest_delta_t_and_choose_top_3_t_sub             10**10   
2         Smallest_delta_t_and_choose_top_3_t_sub             10**11   
3         Smallest_delta_t_and_choose_top_3_t_sub             10**12   
4         Smallest_delta_t_and_choose_top_3_t_sub              10**2   
..                                            ...                ...   
67  Smallest_t_sub_and_filter_by_smallest_delta_t              10**5   
68  Smallest_t_sub_and_filter_by_smallest_delta_t              10**6   
69  Smallest_t_sub_and_filter_by_smallest_delta_t              10**7   
70  Smallest_t_sub_and_filter_by_smallest_delta_t              10**8   
71  Smallest_t_sub_and_filter_by_smallest_delta_t              10**9   

    correlation   p_value  periods_considered  
0           NaN       NaN                18.0  
1     -0.207744  0.174831                18.0  
2     -0.207744  0.174831                18.0  
3     -0.207744  0.174831                18.0  
4           NaN       NaN                18.0  
..          ...       ...                 ...  
67     0.616830  0.024731                18.0  
68     0.616830  0.024731                18.0  
69     0.616830  0.024731                18.0  
70     0.616830  0.024731                18.0  
71     0.616830  0.024731                18.0  

[72 rows x 5 columns]

### Now we can plot linecharts with altair to then see which is the overall best threshhold for each method

In [125]:
import altair as alt

def create_linechart_for_thresholds(x_axis='threshold_exponent',y_axis='correlation',color='subharmonic_method', data_frame=interval_corr_df_w_thresh_period_case,title='Correlation of Subharmonic Tension Scores with Empirical Interval Rankings for Different Thresholds'):
    
   
    sorted_thresholds = ["10**" + str(i) for i in range(1,13)]
    
    line_chart = alt.Chart(data_frame).encode(
        x=alt.X(x_axis, title='Threshold Exponent (10^x)', sort=sorted_thresholds),
        y=alt.Y(y_axis, title='Correlation with Empirical Ranking'),
        color=alt.Color(color,legend=alt.Legend(title='Different Subharmonic Methods',titleAnchor='middle',symbolSize=100)),
        shape=alt.Shape(color,legend=alt.Legend(title='Different Subharmonic Methods',titleAnchor='middle',symbolSize=100)),
        
    )
    return line_chart.mark_line().properties(height=400,width=400,title=title).configure_legend(labelLimit=1000,orient='right', direction='vertical')

    point_chart = alt.Chart(data_frame).encode(
           x=alt.X(x_axis, title='Threshold Exponent (10^x)'),
        y=alt.Y(y_axis, title='Correlation with Empirical Ranking'),
        color=alt.Color(color,legend=alt.Legend(title='Different Subharmonic Methods',titleAnchor='middle',symbolSize=100)),
        shape=alt.Shape(color,legend=alt.Legend(title='Different Subharmonic Methods',titleAnchor='middle',symbolSize=100)),

    )
    return (point_chart.mark_point()+line_chart.mark_line()).properties(height=400,width=400,title=title).configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')

threshold_line_chart = create_linechart_for_thresholds(data_frame=grouped_df_for_correlation.mean(numeric_only=True).reset_index())
threshold_line_chart

alt.Chart(...)

### Based on this, we then choose correlation heatmap with a given threshold

In [126]:
corr_df_to_test = interval_corr_df_w_thresh_period_case[interval_corr_df_w_thresh_period_case['threshold_exponent']=='10**5']
corr_df_to_test = corr_df_to_test[corr_df_to_test['periods_considered']<22]

## Subharmonic Interval Correlation heatmap

In [128]:
corr_chart,text_chart = shm.create_corr_heatmap(corr_df_to_test, x='periods_considered', y='subharmonic_method',  p_value_column='p_value', corr_column='correlation')

interval_chart = (corr_chart+text_chart).properties(width=780, height=200,title='Correlation between Empirical and Computed tension subharmonic rankings for Intervals')
interval_chart

alt.LayerChart(...)

## Line chart for intervals subharmonic correlation and P-value

In [97]:
## Ground truthc
empirical_ranking_numbered = range(0, len(empirical_ranking_intervals))

    
normalized_values_plottable_without_explicit = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]

# normalized_values_num_ranked= [(x - min(empirical_ranking_nums_triads)) / (max(empirical_ranking_nums_triads) - min(empirical_ranking_nums_triads)) for x in empirical_ranking_nums_triads]


df_gt = pd.DataFrame({
    # 'normalized_value_rank_num':normalized_values_num_ranked,
    'chord_label':empirical_ranking_intervals,
    'normalized_value':normalized_values_plottable_without_explicit
})

df_gt['subharmonic_method'] = 'Empirical ranking'


In [129]:
## First we need to norm values and draw a chart that draws a line for the ranking

biggest_df = pd.read_csv('subharmonic_correlation_intervals_for_thresholds_period_case.csv')

## eliminating all that have normed_values_only_modulations
biggest_df = biggest_df[biggest_df['threshold_exponent']=='10**5']

In [130]:

import altair as alt


## also defined in shm.

def correlation_line_point_chart(data_frame,x_axis='periods_considered',y_axis='correlation',color='subharmonic_method'):
    line_chart = alt.Chart(data_frame).mark_line(
    opacity=0.5
    ).encode(
    x=alt.X(x_axis, title='Periods considered to compute Subharmonic Modulation'),
    y=alt.Y(y_axis),
    color=alt.Color(color,legend=None)

    )

    point_chart = alt.Chart(data_frame).mark_point().encode(
      x=alt.X(x_axis, title='Periods considered to compute Subharmonic Modulation',scale=alt.Scale(domain=[4,32])),
    y=alt.Y(y_axis),
    color=alt.Color(color,legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
       shape=alt.Shape(color,legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),

    )
    return line_chart, point_chart


In [154]:




corr_line_chart, corr_point_chart = correlation_line_point_chart(biggest_df,x_axis='periods_considered',y_axis='correlation',color='subharmonic_method')
## we can extract these values of correlation out of the correlation csv 

#.properties(height=400,width=400,title='Correlation with interval ranking for subharmonic each method').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='independent',shape='independent')#.resolve_legend(color='independent',shape='independent')

merged = (corr_point_chart+corr_line_chart).resolve_scale(color='independent',shape='independent').properties(height=400,width=400)
p_val_line_chart, p_val_point_chart = correlation_line_point_chart(biggest_df,x_axis='periods_considered',y_axis='p_value',color='subharmonic_method')


merged_pval = (p_val_point_chart+p_val_line_chart).resolve_scale(color='independent',shape='independent').properties(height=400,width=400)

## zooming on the important p-values
merged_pval = merged_pval.encode(
    y=alt.Y('p_value', scale=alt.Scale(domain=[0.1, 0], clamp=True))
)

interval_corr_pval_chart = alt.vconcat(merged, merged_pval).properties(title='Correlation and P-values with interval ranking for each subharmonic method').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared',shape='shared')
interval_corr_pval_chart
## create big dataframe for line chart

alt.VConcatChart(...)

In [174]:
periods_considered = 11



## get df for each interval

df_per_chord_label = ihm.convert_correlation_df_to_a_line_chart_df(biggest_df,empirical_ranking_names=empirical_ranking_intervals,column_to_convert='scores_based_on_emp_rank',group_by_methods_array=['subharmonic_method','periods_considered'])
df_per_chord_label

Normalized values for each rank: [0.0, 0.1310116144078594, 0.11467511762126212, 0.19511567756893125, 0.15861995117587668, 0.1597428239254548, 0.08521910176579284, 0.1580093145386703, 0.16724794352536118, 0.2023952518623577, 0.25777164878007836, 0.18238764679065278, 1.0]
Normalized values for each rank: [0.0, 0.041622680076453436, 0.040296385875744606, 0.04801992628497836, 0.04827081182832273, 0.07566291657764933, 0.08521910176579284, 0.0957976070652699, 0.04497675562319077, 0.06311042439940451, 0.25777164878007836, 0.05129848289180853, 1.0]
Normalized values for each rank: [0.0, 0.041622680076453436, 0.040296385875744606, 0.08058194313796654, 0.09461247217482213, 0.07566291657764933, 0.08521910176579284, 0.11815449409492772, 0.06348395998370564, 0.06311042439940451, 0.25777164878007836, 0.05129848289180853, 1.0]
Normalized values for each rank: [0.0, 0.2040163720794325, 0.20073959717939213, 0.28386958825835246, 0.30759140458540474, 0.2750689305931321, 0.2919231093383887, 0.343736082038

chord_label  normalized_value  \
0              U          0.000000   
1             8v          0.131012   
2             P5          0.114675   
3             P4          0.195116   
4             M3          0.158620   
...          ...               ...   
2257          TT          0.079632   
2258          m7          0.202395   
2259          M2          0.257772   
2260          M7          0.182388   
2261          m2          1.000000   

                                 subharmonic_method  periods_considered  
0           Smallest_delta_t_and_choose_top_3_t_sub                   4  
1           Smallest_delta_t_and_choose_top_3_t_sub                   4  
2           Smallest_delta_t_and_choose_top_3_t_sub                   4  
3           Smallest_delta_t_and_choose_top_3_t_sub                   4  
4           Smallest_delta_t_and_choose_top_3_t_sub                   4  
...                                             ...                 ...  
2257  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2258  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2259  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2260  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2261  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  

[2262 rows x 4 columns]

In [175]:
periods_considered=11

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['periods_considered']==periods_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_intervals),
    y='normalized_value',
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
    shape=alt.Shape('subharmonic_method',legend=None)
)
(line_chart.mark_line(opacity=0.6) + line_chart.mark_point()).resolve_scale(color='shared',shape='shared').properties(height=400,width=400).configure_legend(labelLimit=1000)

alt.LayerChart(...)

In [180]:
periods_considered=11

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['periods_considered']==periods_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_intervals),
    y='normalized_value',
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
line_charts = (line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape=alt.Shape('subharmonic_method',legend=None)))


chart_gt = alt.Chart(df_gt).encode(
   x=alt.X('chord_label', sort=empirical_ranking_intervals),
    y='normalized_value',
).mark_line(
    color='black'
)
(line_charts+chart_gt).properties(width=300,height=300,title=f'Overall interharmonic tension ratings for triads ranked ({periods_considered} periods considered)').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='independent',shape='independent')


alt.LayerChart(...)

# Subharmonic Triads Correlation


In [68]:
triad_subharmonic_w_threshholds = pipeline_for_threshold_considered(notes_to_consider=triads,chord_labels=chord_labels_triads,threshold_exponents=threshold_exponents,periods_considered=periods_considered)
triad_subharmonic_w_threshholds

Now processing threshold exponent 1
Now processing threshold exponent 2
Now processing threshold exponent 3
Now processing threshold exponent 4
Now processing threshold exponent 5
Now processing threshold exponent 6
Now processing threshold exponent 7
Now processing threshold exponent 8
Now processing threshold exponent 9
Now processing threshold exponent 10
Now processing threshold exponent 11
Now processing threshold exponent 12


t_values  mean_t_sub  \
0    [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
1    [0.00382225643297143, 0.003033726941295533, 0....    0.003986   
2    [0.00764451286594286, 0.006067453882591066, 0....    0.006271   
3    [0.00382225643297143, 0.003033726941295533, 0....    0.003136   
4    [0.00764451286594286, 0.009101180823886598, 0....    0.008133   
..                                                 ...         ...   
229  [0.05733384649457145, 0.057640811884615124, 0....    0.057588   
230  [0.06880061579348574, 0.06977571964979726, 0.0...    0.069468   
231  [0.04586707719565716, 0.04550590411943299, 0.0...    0.045708   
232  [0.05733384649457145, 0.057640811884615124, 0....    0.057588   
233  [0.06880061579348574, 0.06977571964979726, 0.0...    0.069468   

              indices  difference_(delta_t)  difference_ratio_(delta_t_hat)  \
0       [0.0, 0, 0.0]              0.001271                        0.405401   
1       [0.0, 0, 1.0]              0.002068                        0.518906   
2       [1.0, 1, 1.0]              0.002542                        0.405401   
3       [0.0, 0, 0.0]              0.001271                        0.405401   
4       [1.0, 2, 2.0]              0.001457                        0.179107   
..                ...                   ...                             ...   
229  [14.0, 18, 23.0]              0.000455                        0.007902   
230  [17.0, 22, 28.0]              0.001028                        0.014793   
231  [11.0, 14, 18.0]              0.000361                        0.007902   
232  [14.0, 18, 23.0]              0.000455                        0.007902   
233  [17.0, 22, 28.0]              0.001028                        0.014793   

                                                  case  tension_score  \
0              Smallest_t_sub_and_choose_top_3_delta_t       0.000000   
1              Smallest_t_sub_and_choose_top_3_delta_t       0.000000   
2              Smallest_t_sub_and_choose_top_3_delta_t       0.000000   
3              Smallest_delta_t_and_choose_top_3_t_sub       0.000000   
4              Smallest_delta_t_and_choose_top_3_t_sub       0.000000   
..                                                 ...            ...   
229        Smallest_ratio_and_filter_by_smallest_t_sub  492215.648063   
230        Smallest_ratio_and_filter_by_smallest_t_sub  492215.648063   
231  Smallest_ratio_and_filter_by_smallest_t_sub_wi...     701.580821   
232  Smallest_ratio_and_filter_by_smallest_t_sub_wi...     701.580821   
233  Smallest_ratio_and_filter_by_smallest_t_sub_wi...     701.580821   

    note_names chord_label  normalized_tension_score  periods_considered  \
0     C4,E4,G4          CM                  0.000000                   4   
1     C4,E4,G4          CM                  0.000000                   4   
2     C4,E4,G4          CM                  0.000000                   4   
3     C4,E4,G4          CM                  0.000000                   4   
4     C4,E4,G4          CM                  0.000000                   4   
..         ...         ...                       ...                 ...   
229  C4,E4,G#4        CAug                  0.014310                  32   
230  C4,E4,G#4        CAug                  0.014310                  32   
231  C4,E4,G#4        CAug                  0.052108                  32   
232  C4,E4,G#4        CAug                  0.052108                  32   
233  C4,E4,G#4        CAug                  0.052108                  32   

    threshold_exponent  
0                10**1  
1                10**1  
2                10**1  
3                10**1  
4                10**1  
..                 ...  
229             10**12  
230             10**12  
231             10**12  
232             10**12  
233             10**12  

[81432 rows x 12 columns]

In [69]:
# triad_subharmonic = pipeline_for_subharmonic_normalized_tension_score(notes_to_consider=triads,chord_labels=chord_labels_triads)
# triad_subharmonic

In [70]:
## first clean the top_m things

triad_grouped_df = triad_subharmonic_w_threshholds.drop(['t_values','mean_t_sub','indices', 'difference_(delta_t)', 'difference_ratio_(delta_t_hat)'], axis=1)
triad_grouped_df = triad_grouped_df.groupby(['case','note_names','periods_considered','threshold_exponent']).first().reset_index()
triad_grouped_df

case note_names  \
0            Smallest_delta_t_and_choose_top_3_t_sub  C4,D#4,A4   
1            Smallest_delta_t_and_choose_top_3_t_sub  C4,D#4,A4   
2            Smallest_delta_t_and_choose_top_3_t_sub  C4,D#4,A4   
3            Smallest_delta_t_and_choose_top_3_t_sub  C4,D#4,A4   
4            Smallest_delta_t_and_choose_top_3_t_sub  C4,D#4,A4   
...                                              ...        ...   
27139  Smallest_t_sub_and_filter_by_smallest_delta_t   C4,F4,G4   
27140  Smallest_t_sub_and_filter_by_smallest_delta_t   C4,F4,G4   
27141  Smallest_t_sub_and_filter_by_smallest_delta_t   C4,F4,G4   
27142  Smallest_t_sub_and_filter_by_smallest_delta_t   C4,F4,G4   
27143  Smallest_t_sub_and_filter_by_smallest_delta_t   C4,F4,G4   

       periods_considered threshold_exponent  tension_score chord_label  \
0                       4              10**1       0.000000     Adim1st   
1                       4             10**10    8513.101364     Adim1st   
2                       4             10**11    8513.101364     Adim1st   
3                       4             10**12    8513.101364     Adim1st   
4                       4              10**2       0.000000     Adim1st   
...                   ...                ...            ...         ...   
27139                  32              10**5    8827.264915       Csus4   
27140                  32              10**6    8827.264915       Csus4   
27141                  32              10**7    8827.264915       Csus4   
27142                  32              10**8    8827.264915       Csus4   
27143                  32              10**9    8827.264915       Csus4   

       normalized_tension_score  
0                      0.000000  
1                      0.183563  
2                      0.183563  
3                      0.183563  
4                      0.000000  
...                         ...  
27139                  0.799136  
27140                  0.799136  
27141                  0.799136  
27142                  0.799136  
27143                  0.799136  

[27144 rows x 7 columns]

In [72]:
# ## now save csv with scores

# import psychoacoustic_tension_chan_module.subharmonic_module as shm
triad_grouped_df.to_csv('overall_subharmonic_tension_triads_with_tension_score_normalized_per_period_per_threshold.csv')
# triad_grouped_df = pd.read_csv('overall_subharmonic_tension_triads_with_tension_score_normalized_per_period_per_threshold.csv')

## Linechart of average correlation per threshold

After computing all possible thresholds and tension scores, we should now average each correlationand plot a linechart, to see, for each case (color) what is the average correlation (y axis) given threshold (x axis)

In [74]:
triad_corr_df_w_thresh_period_case = create_corr_df_for_subharmonic_per_threshold(triad_grouped_df,empirical_ranking=empirical_ranking_triads,empirical_ranking_num=None, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')

Now processing threshold 10**1


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**10
Now processing threshold 10**11
Now processing threshold 10**12
Now processing threshold 10**2


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**3


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**4


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**5
Now processing threshold 10**6
Now processing threshold 10**7
Now processing threshold 10**8
Now processing threshold 10**9


In [75]:
triad_corr_df_w_thresh_period_case.to_csv('subharmonic_correlation_triads_for_thresholds_period_case.csv')
triad_corr_df_w_thresh_period_case


correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
2083    -0.554048  [0.725158360019106, 0.0611414614452801, 1.0, 0...   
2084    -0.095615  [0.07972992747688716, 0.053326487885543956, 0....   
2085    -0.235666  [0.2039886417326898, 0.15192244888553638, 0.26...   
2086    -0.002458  [0.5498627292790443, 0.7613911099998745, 0.147...   
2087     0.059129  [0.09056755766514307, 0.43292915617455824, 0.1...   

       p_value                                 subharmonic_method  \
0          NaN            Smallest_delta_t_and_choose_top_3_t_sub   
1          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2          NaN        Smallest_ratio_and_filter_by_smallest_t_sub   
3          NaN  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
4          NaN            Smallest_t_sub_and_choose_top_3_delta_t   
...        ...                                                ...   
2083  0.049448  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2084  0.756013        Smallest_ratio_and_filter_by_smallest_t_sub   
2085  0.438279  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
2086  0.993642            Smallest_t_sub_and_choose_top_3_delta_t   
2087  0.847839      Smallest_t_sub_and_filter_by_smallest_delta_t   

      periods_considered threshold_exponent  
0                      4              10**1  
1                      4              10**1  
2                      4              10**1  
3                      4              10**1  
4                      4              10**1  
...                  ...                ...  
2083                  32              10**9  
2084                  32              10**9  
2085                  32              10**9  
2086                  32              10**9  
2087                  32              10**9  

[2088 rows x 6 columns]

### Now read and plor linechart to see which is best threshold

In [81]:
triad_corr_df_w_thresh_period_case = pd.read_csv('subharmonic_correlation_triads_for_thresholds_period_case.csv')
triad_corr_df_w_thresh_period_case.drop(columns=['Unnamed: 0'], inplace=True)
grouped_df_for_correlation = triad_corr_df_w_thresh_period_case.groupby(['subharmonic_method','threshold_exponent'])
grouped_df_for_correlation.mean(numeric_only=True).reset_index()

subharmonic_method threshold_exponent  \
0         Smallest_delta_t_and_choose_top_3_t_sub              10**1   
1         Smallest_delta_t_and_choose_top_3_t_sub             10**10   
2         Smallest_delta_t_and_choose_top_3_t_sub             10**11   
3         Smallest_delta_t_and_choose_top_3_t_sub             10**12   
4         Smallest_delta_t_and_choose_top_3_t_sub              10**2   
..                                            ...                ...   
67  Smallest_t_sub_and_filter_by_smallest_delta_t              10**5   
68  Smallest_t_sub_and_filter_by_smallest_delta_t              10**6   
69  Smallest_t_sub_and_filter_by_smallest_delta_t              10**7   
70  Smallest_t_sub_and_filter_by_smallest_delta_t              10**8   
71  Smallest_t_sub_and_filter_by_smallest_delta_t              10**9   

    correlation   p_value  periods_considered  
0           NaN       NaN                18.0  
1     -0.187457  0.409656                18.0  
2     -0.187457  0.409656                18.0  
3     -0.187457  0.409656                18.0  
4           NaN       NaN                18.0  
..          ...       ...                 ...  
67     0.059129  0.847839                18.0  
68     0.059129  0.847839                18.0  
69     0.059129  0.847839                18.0  
70     0.059129  0.847839                18.0  
71     0.059129  0.847839                18.0  

[72 rows x 5 columns]

In [77]:
threshold_line_chart = create_linechart_for_thresholds(data_frame=grouped_df_for_correlation.mean(numeric_only=True).reset_index())
threshold_line_chart

alt.Chart(...)

In [83]:
# without real scores
triad_corr_df_rank_only = create_corr_df_for_subharmonic_per_threshold(triad_grouped_df,empirical_ranking=empirical_ranking_triads,empirical_ranking_num=None, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')
triad_corr_df_with_emp_num = create_corr_df_for_subharmonic_per_threshold(triad_grouped_df,empirical_ranking=empirical_ranking_triads,empirical_ranking_num=empirical_ranking_nums_triads, labels_to_compare_with_rank='chord_label',column_to_compare_with_rank='normalized_tension_score',break_into_methods='case',periods='periods_considered')

Now processing threshold 10**1


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**10
Now processing threshold 10**11
Now processing threshold 10**12
Now processing threshold 10**2


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**3


...

Now processing threshold 10**3


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**4


c:\Users\gabri\OneDrive\Documents\Tension_visualization_tool\psychoacoustic_tension_science\psychoacoustic_tension_chan_module\dataframe_functions_for_functionality.py:428: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  corr, p_value = stats.pearsonr(normalized_values, values_to_correlate)


Now processing threshold 10**5
Now processing threshold 10**6
Now processing threshold 10**7
Now processing threshold 10**8
Now processing threshold 10**9


### Now that we have rank only and numerical rank, lets put them in csvs, and plot them as well. 

In [85]:
triad_corr_df_rank_only.to_csv('subharmonic_correlation_triads_for_thresholds_period_case_with_rank_only.csv')
triad_corr_df_with_emp_num.to_csv('subharmonic_correlation_triads_for_thresholds_period_case_with_empirical_numbers.csv')

### Now read and plor linechart to see which is best threshold

In [86]:
triad_corr_df_w_thresh_period_case = pd.read_csv('subharmonic_correlation_triads_for_thresholds_period_case_with_rank_only.csv')
triad_corr_df_w_thresh_period_case.drop(columns=['Unnamed: 0'], inplace=True)
grouped_df_for_correlation = triad_corr_df_w_thresh_period_case.groupby(['subharmonic_method','threshold_exponent'])
grouped_df_for_correlation.mean(numeric_only=True).reset_index()

subharmonic_method threshold_exponent  \
0         Smallest_delta_t_and_choose_top_3_t_sub              10**1   
1         Smallest_delta_t_and_choose_top_3_t_sub             10**10   
2         Smallest_delta_t_and_choose_top_3_t_sub             10**11   
3         Smallest_delta_t_and_choose_top_3_t_sub             10**12   
4         Smallest_delta_t_and_choose_top_3_t_sub              10**2   
..                                            ...                ...   
67  Smallest_t_sub_and_filter_by_smallest_delta_t              10**5   
68  Smallest_t_sub_and_filter_by_smallest_delta_t              10**6   
69  Smallest_t_sub_and_filter_by_smallest_delta_t              10**7   
70  Smallest_t_sub_and_filter_by_smallest_delta_t              10**8   
71  Smallest_t_sub_and_filter_by_smallest_delta_t              10**9   

    correlation   p_value  periods_considered  
0           NaN       NaN                18.0  
1     -0.187457  0.409656                18.0  
2     -0.187457  0.409656                18.0  
3     -0.187457  0.409656                18.0  
4           NaN       NaN                18.0  
..          ...       ...                 ...  
67     0.059129  0.847839                18.0  
68     0.059129  0.847839                18.0  
69     0.059129  0.847839                18.0  
70     0.059129  0.847839                18.0  
71     0.059129  0.847839                18.0  

[72 rows x 5 columns]

In [87]:
threshold_line_chart = create_linechart_for_thresholds(data_frame=grouped_df_for_correlation.mean(numeric_only=True).reset_index())
threshold_line_chart

alt.Chart(...)

In [112]:
triad_corr_df_w_thresh_period_case = pd.read_csv('subharmonic_correlation_triads_for_thresholds_period_case_with_empirical_numbers.csv')
triad_corr_df_w_thresh_period_case.drop(columns=['Unnamed: 0'], inplace=True)
grouped_df_for_correlation = triad_corr_df_w_thresh_period_case.groupby(['subharmonic_method','threshold_exponent'])
grouped_df_for_correlation.mean(numeric_only=True).reset_index()

subharmonic_method threshold_exponent  \
0         Smallest_delta_t_and_choose_top_3_t_sub              10**1   
1         Smallest_delta_t_and_choose_top_3_t_sub             10**10   
2         Smallest_delta_t_and_choose_top_3_t_sub             10**11   
3         Smallest_delta_t_and_choose_top_3_t_sub             10**12   
4         Smallest_delta_t_and_choose_top_3_t_sub              10**2   
..                                            ...                ...   
67  Smallest_t_sub_and_filter_by_smallest_delta_t              10**5   
68  Smallest_t_sub_and_filter_by_smallest_delta_t              10**6   
69  Smallest_t_sub_and_filter_by_smallest_delta_t              10**7   
70  Smallest_t_sub_and_filter_by_smallest_delta_t              10**8   
71  Smallest_t_sub_and_filter_by_smallest_delta_t              10**9   

    correlation   p_value  periods_considered  
0           NaN       NaN                18.0  
1     -0.173182  0.400976                18.0  
2     -0.173182  0.400976                18.0  
3     -0.173182  0.400976                18.0  
4           NaN       NaN                18.0  
..          ...       ...                 ...  
67    -0.025800  0.933325                18.0  
68    -0.025800  0.933325                18.0  
69    -0.025800  0.933325                18.0  
70    -0.025800  0.933325                18.0  
71    -0.025800  0.933325                18.0  

[72 rows x 5 columns]

In [113]:
threshold_line_chart = create_linechart_for_thresholds(data_frame=grouped_df_for_correlation.mean(numeric_only=True).reset_index())
threshold_line_chart

alt.Chart(...)

### Now that we know best threshold, now see corr dfs

In [114]:
triad_corr_df_w_thresh_period_case = triad_corr_df_w_thresh_period_case[triad_corr_df_w_thresh_period_case['threshold_exponent']=='10**5']

In [115]:
corr_chart,text_chart = shm.create_corr_heatmap(triad_corr_df_w_thresh_period_case, x='periods_considered', y='subharmonic_method',  p_value_column='p_value', corr_column='correlation')

triad_emp_num_chart = (corr_chart+text_chart).properties(width=1200, height=150,title='Correlation between Empirical and Computed tension subharmonic rankings for Intervals (based on numbers)').configure_title(anchor='start',align='left')
triad_emp_num_chart

alt.LayerChart(...)

In [134]:
### With only rankings
triad_corr_df_w_thresh_period_case = pd.read_csv('subharmonic_correlation_triads_for_thresholds_period_case_with_rank_only.csv')
triad_corr_df_w_thresh_period_case.drop(columns=['Unnamed: 0'], inplace=True)
triad_corr_df_w_thresh_period_case


correlation                           scores_based_on_emp_rank  \
0             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
1             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
2             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
3             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
4             NaN  [0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, ...   
...           ...                                                ...   
2083    -0.554048  [0.725158360019106, 0.0611414614452801, 1.0, 0...   
2084    -0.095615  [0.07972992747688716, 0.053326487885543956, 0....   
2085    -0.235666  [0.2039886417326898, 0.15192244888553638, 0.26...   
2086    -0.002458  [0.5498627292790443, 0.7613911099998745, 0.147...   
2087     0.059129  [0.09056755766514307, 0.43292915617455824, 0.1...   

       p_value                                 subharmonic_method  \
0          NaN            Smallest_delta_t_and_choose_top_3_t_sub   
1          NaN  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2          NaN        Smallest_ratio_and_filter_by_smallest_t_sub   
3          NaN  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
4          NaN            Smallest_t_sub_and_choose_top_3_delta_t   
...        ...                                                ...   
2083  0.049448  Smallest_delta_t_and_filter_by_smallest_t_sub_...   
2084  0.756013        Smallest_ratio_and_filter_by_smallest_t_sub   
2085  0.438279  Smallest_ratio_and_filter_by_smallest_t_sub_wi...   
2086  0.993642            Smallest_t_sub_and_choose_top_3_delta_t   
2087  0.847839      Smallest_t_sub_and_filter_by_smallest_delta_t   

      periods_considered threshold_exponent  
0                      4              10**1  
1                      4              10**1  
2                      4              10**1  
3                      4              10**1  
4                      4              10**1  
...                  ...                ...  
2083                  32              10**9  
2084                  32              10**9  
2085                  32              10**9  
2086                  32              10**9  
2087                  32              10**9  

[2088 rows x 6 columns]

In [135]:
triad_corr_df_w_thresh_period_case = triad_corr_df_w_thresh_period_case[triad_corr_df_w_thresh_period_case['threshold_exponent']=='10**5']
triad_corr_df_w_thresh_period_case = triad_corr_df_w_thresh_period_case[triad_corr_df_w_thresh_period_case['periods_considered']<=24]


In [140]:
corr_chart,text_chart = shm.create_corr_heatmap(triad_corr_df_w_thresh_period_case, x='periods_considered', y='subharmonic_method',  p_value_column='p_value', corr_column='correlation')

triad_sub_chart = (corr_chart+text_chart).properties(width=790, height=150,title='Correlation between Empirical and Computed tension subharmonic rankings for Triads').configure_title(anchor='middle',align='left')
triad_sub_chart

alt.LayerChart(...)

In [98]:
## Ground truthc
empirical_ranking_numbered = range(0, len(empirical_ranking_triads))

    
normalized_values_plottable_without_explicit = [x / max(empirical_ranking_numbered) for x in empirical_ranking_numbered]

normalized_values_num_ranked= [(x - min(empirical_ranking_nums_triads)) / (max(empirical_ranking_nums_triads) - min(empirical_ranking_nums_triads)) for x in empirical_ranking_nums_triads]


df_gt = pd.DataFrame({
    'normalized_value_rank_num':normalized_values_num_ranked,
    'chord_label':empirical_ranking_triads,
    'normalized_value':normalized_values_plottable_without_explicit
})

df_gt['method'] = 'Empirical ranking'


In [99]:
## First we need to norm values and draw a chart that draws a line for the ranking

biggest_df = pd.read_csv('subharmonic_tension_triads_correlation_with_empirical_ranking_number.csv')

## eliminating all that have normed_values_only_modulations
biggest_df

Unnamed: 0  correlation  \
0             0    -0.267263   
1             1     0.404310   
2             2     0.193157   
3             3     0.192873   
4             4    -0.066339   
..          ...          ...   
169         169    -0.520826   
170         170    -0.115147   
171         171    -0.229494   
172         172    -0.066339   
173         173    -0.025800   

                              scores_based_on_emp_rank   p_value  \
0    [0.4360836390113848, 0.5215672664959862, 0.005...  0.377371   
1    [0.0, 0.1109198724250039, 0.4132178027279304, ...  0.170611   
2    [0.437793656875681, 0.5341969182503766, 0.3064...  0.527216   
3    [0.4676045840605338, 0.5636484078743014, 0.333...  0.527833   
4    [0.5498627292790443, 0.7613911099998745, 0.147...  0.829515   
..                                                 ...       ...   
169  [0.725158360019106, 0.0611414614452801, 1.0, 0...  0.068006   
170  [0.0797299274768871, 0.0533264878855439, 0.114...  0.707970   
171  [0.2039886417326898, 0.1519224488855363, 0.262...  0.450711   
172  [0.5498627292790443, 0.7613911099998745, 0.147...  0.829515   
173  [0.090567557665143, 0.4329291561745582, 0.1540...  0.933325   

                                    subharmonic_method  periods_considered  
0              Smallest_delta_t_and_choose_top_3_t_sub                   4  
1    Smallest_delta_t_and_filter_by_smallest_t_sub_...                   4  
2          Smallest_ratio_and_filter_by_smallest_t_sub                   4  
3    Smallest_ratio_and_filter_by_smallest_t_sub_wi...                   4  
4              Smallest_t_sub_and_choose_top_3_delta_t                   4  
..                                                 ...                 ...  
169  Smallest_delta_t_and_filter_by_smallest_t_sub_...                  32  
170        Smallest_ratio_and_filter_by_smallest_t_sub                  32  
171  Smallest_ratio_and_filter_by_smallest_t_sub_wi...                  32  
172            Smallest_t_sub_and_choose_top_3_delta_t                  32  
173      Smallest_t_sub_and_filter_by_smallest_delta_t                  32  

[174 rows x 6 columns]

In [100]:

    # method_not_allowed = [] 
    # for unique_method in biggest_df.method.unique():
    #     if 'Experiment' in unique_method and 'normed_values_only_modulations' in unique_method:
    #         method_not_allowed.append(unique_method)
            
    # method_not_allowed

In [101]:

# ## eliminating all that have normed_values_only_modulations

# method_not_allowed = [] 
# for unique_method in biggest_df.method.unique():
#     if 'Experiment' in unique_method and 'normed_values_only_modulations' in unique_method:
#         method_not_allowed.append(unique_method)
        
# method_not_allowed

In [102]:


# biggest_df =biggest_df[~biggest_df.method.isin(method_not_allowed)]

In [103]:

import altair as alt


## then we need to plot lines based on those values. 

line_chart = alt.Chart(biggest_df).mark_line(
    opacity=0.5
).encode(
    x=alt.X('periods_considered', title='Periods considered to compute Interharmonic Modulation'),
    y=alt.Y('correlation'),
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
    
)
line_chart
## we can extract these values of correlation out of the correlation csv 

## Take the column and assign the x to each y, and plot. 

## create big dataframe for line chart

alt.Chart(...)

In [104]:
point_chart = alt.Chart(biggest_df).encode(
      x=alt.X('periods_considered', title='Periods considered to compute Subharmonic Modulation',scale=alt.Scale(domain=[4,32])),
    y=alt.Y('correlation'),
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
       shape=alt.Shape('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),

)
point_chart.mark_point()

alt.Chart(...)

In [106]:
triad_emp_line_chart = (point_chart.mark_point()+line_chart).configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared').properties(height=350,width=350,title='Correlation with interval ranking for each method using empirical ranking numbers').configure_axisY(title='Correlation with Empirical Ranking Numbers')
triad_emp_line_chart

alt.LayerChart(...)

## Subharmonic triad line corr chart

In [109]:
triad_emp_line_chart

alt.LayerChart(...)

In [110]:
periods_considered = 6



## get df for each interval

df_per_chord_label = ihm.convert_correlation_df_to_a_line_chart_df(biggest_df,empirical_ranking_names=empirical_ranking_triads,column_to_convert='scores_based_on_emp_rank',group_by_methods_array=['subharmonic_method','periods_considered'])
df_per_chord_label

Normalized values for each rank: [0.4360836390113848, 0.5215672664959862, 0.0054168512343302, 0.0865582199744762, 0.1542894115641612, 1.0, 0.916177907926823, 0.3429978701000641, 0.1835630551170576, 0.0792408169422637, 0.2798141017514379, 0.4625279294380351, 0.0]
Normalized values for each rank: [0.0, 0.1109198724250039, 0.4132178027279304, 0.3359505851343858, 0.9271623545075448, 0.2360400456523284, 0.1539602625028244, 0.707350328093148, 1.0, 0.6135942229486009, 0.7999956848164618, 0.1552382297217608, 0.5432648925314469]
Normalized values for each rank: [0.437793656875681, 0.5341969182503766, 0.3064365995290753, 0.2151084808024977, 0.9139075361779938, 0.713836286110211, 0.0, 0.6540946495343206, 1.0, 0.5432770354327604, 0.7635993839069457, 0.7977052869162626, 0.4601493437888573]
Normalized values for each rank: [0.4676045840605338, 0.5636484078743014, 0.3330349883675894, 0.2367463556934985, 0.9224715345820876, 0.7370443314412654, 0.0, 0.680145201239459, 1.0, 0.5725827769772874, 0.7838855

chord_label  normalized_value  \
0             CM          0.436084   
1             Cm          0.521567   
2          FM2nd          0.005417   
3       Fsus42nd          0.086558   
4         G#M1st          0.154289   
...          ...               ...   
2257     Adim1st          0.698707   
2258       Am1st          0.379744   
2259    F#dim2nd          0.992992   
2260        Cdim          0.000000   
2261        CAug          0.137467   

                                 subharmonic_method  periods_considered  
0           Smallest_delta_t_and_choose_top_3_t_sub                   4  
1           Smallest_delta_t_and_choose_top_3_t_sub                   4  
2           Smallest_delta_t_and_choose_top_3_t_sub                   4  
3           Smallest_delta_t_and_choose_top_3_t_sub                   4  
4           Smallest_delta_t_and_choose_top_3_t_sub                   4  
...                                             ...                 ...  
2257  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2258  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2259  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2260  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2261  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  

[2262 rows x 4 columns]

In [111]:
harmonics_considered=6

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['periods_considered']==periods_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
(line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='subharmonic_method')).properties(height=600,width=600)

alt.LayerChart(...)

In [113]:
periods_considered=14

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['periods_considered']==periods_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
line_charts = (line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='subharmonic_method'))


chart_gt = alt.Chart(df_gt).encode(
   x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value_rank_num',
).mark_line(
    color='black'
)
(line_charts+chart_gt).properties(width=400,height=400,title='Overall interharmonic tension ratings for triads ranked (periods considered = 14)').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')


alt.LayerChart(...)

In [114]:
## First we need to norm values and draw a chart that draws a line for the ranking

biggest_df = pd.read_csv('subharmonic_tension_triads_correlation_with_rank_only.csv')

## eliminating all that have normed_values_only_modulations
biggest_df


Unnamed: 0  correlation  \
0             0    -0.161602   
1             1     0.420376   
2             2     0.329149   
3             3     0.325379   
4             4    -0.002458   
..          ...          ...   
169         169    -0.554048   
170         170    -0.095615   
171         171    -0.235666   
172         172    -0.002458   
173         173     0.059129   

                              scores_based_on_emp_rank   p_value  \
0    [0.4360836390113848, 0.5215672664959862, 0.005...  0.597885   
1    [0.0, 0.1109198724250039, 0.4132178027279304, ...  0.152643   
2    [0.437793656875681, 0.5341969182503766, 0.3064...  0.272139   
3    [0.4676045840605338, 0.5636484078743014, 0.333...  0.277997   
4    [0.5498627292790443, 0.7613911099998745, 0.147...  0.993642   
..                                                 ...       ...   
169  [0.725158360019106, 0.0611414614452801, 1.0, 0...  0.049448   
170  [0.0797299274768871, 0.0533264878855439, 0.114...  0.756013   
171  [0.2039886417326898, 0.1519224488855363, 0.262...  0.438279   
172  [0.5498627292790443, 0.7613911099998745, 0.147...  0.993642   
173  [0.090567557665143, 0.4329291561745582, 0.1540...  0.847839   

                                    subharmonic_method  periods_considered  
0              Smallest_delta_t_and_choose_top_3_t_sub                   4  
1    Smallest_delta_t_and_filter_by_smallest_t_sub_...                   4  
2          Smallest_ratio_and_filter_by_smallest_t_sub                   4  
3    Smallest_ratio_and_filter_by_smallest_t_sub_wi...                   4  
4              Smallest_t_sub_and_choose_top_3_delta_t                   4  
..                                                 ...                 ...  
169  Smallest_delta_t_and_filter_by_smallest_t_sub_...                  32  
170        Smallest_ratio_and_filter_by_smallest_t_sub                  32  
171  Smallest_ratio_and_filter_by_smallest_t_sub_wi...                  32  
172            Smallest_t_sub_and_choose_top_3_delta_t                  32  
173      Smallest_t_sub_and_filter_by_smallest_delta_t                  32  

[174 rows x 6 columns]

In [115]:

import altair as alt


## then we need to plot lines based on those values. 

line_chart = alt.Chart(biggest_df).mark_line(
    opacity=0.5
).encode(
    x=alt.X('periods_considered', title='Periods considered to compute Interharmonic Modulation'),
    y=alt.Y('correlation'),
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
    
)
line_chart


alt.Chart(...)

In [116]:

## we can extract these values of correlation out of the correlation csv 

## Take the column and assign the x to each y, and plot. 

## create big dataframe for line chart
point_chart = alt.Chart(biggest_df).encode(
      x=alt.X('periods_considered', title='Periods considered to compute Subharmonic Modulation',scale=alt.Scale(domain=[4,32])),
    y=alt.Y('correlation'),
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),
       shape=alt.Shape('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100)),

)
point_chart.mark_point()
(point_chart.mark_point()+line_chart).properties(height=400,width=400,title='Correlation with interval ranking for each method').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')



alt.LayerChart(...)

In [118]:

periods_considered = 14



## get df for each interval

df_per_chord_label = ihm.convert_correlation_df_to_a_line_chart_df(biggest_df,empirical_ranking_names=empirical_ranking_triads,column_to_convert='scores_based_on_emp_rank',group_by_methods_array=['subharmonic_method','periods_considered'])
df_per_chord_label



Normalized values for each rank: [0.4360836390113848, 0.5215672664959862, 0.0054168512343302, 0.0865582199744762, 0.1542894115641612, 1.0, 0.916177907926823, 0.3429978701000641, 0.1835630551170576, 0.0792408169422637, 0.2798141017514379, 0.4625279294380351, 0.0]
Normalized values for each rank: [0.0, 0.1109198724250039, 0.4132178027279304, 0.3359505851343858, 0.9271623545075448, 0.2360400456523284, 0.1539602625028244, 0.707350328093148, 1.0, 0.6135942229486009, 0.7999956848164618, 0.1552382297217608, 0.5432648925314469]
Normalized values for each rank: [0.437793656875681, 0.5341969182503766, 0.3064365995290753, 0.2151084808024977, 0.9139075361779938, 0.713836286110211, 0.0, 0.6540946495343206, 1.0, 0.5432770354327604, 0.7635993839069457, 0.7977052869162626, 0.4601493437888573]
Normalized values for each rank: [0.4676045840605338, 0.5636484078743014, 0.3330349883675894, 0.2367463556934985, 0.9224715345820876, 0.7370443314412654, 0.0, 0.680145201239459, 1.0, 0.5725827769772874, 0.7838855

chord_label  normalized_value  \
0             CM          0.436084   
1             Cm          0.521567   
2          FM2nd          0.005417   
3       Fsus42nd          0.086558   
4         G#M1st          0.154289   
...          ...               ...   
2257     Adim1st          0.698707   
2258       Am1st          0.379744   
2259    F#dim2nd          0.992992   
2260        Cdim          0.000000   
2261        CAug          0.137467   

                                 subharmonic_method  periods_considered  
0           Smallest_delta_t_and_choose_top_3_t_sub                   4  
1           Smallest_delta_t_and_choose_top_3_t_sub                   4  
2           Smallest_delta_t_and_choose_top_3_t_sub                   4  
3           Smallest_delta_t_and_choose_top_3_t_sub                   4  
4           Smallest_delta_t_and_choose_top_3_t_sub                   4  
...                                             ...                 ...  
2257  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2258  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2259  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2260  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  
2261  Smallest_t_sub_and_filter_by_smallest_delta_t                  32  

[2262 rows x 4 columns]

In [119]:

harmonics_considered=6

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['periods_considered']==periods_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
(line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='subharmonic_method')).properties(height=600,width=600)



alt.LayerChart(...)

In [ ]:

periods_considered=14

line_chart =alt.Chart(df_per_chord_label[df_per_chord_label['periods_considered']==periods_considered]).encode(
    x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
    color=alt.Color('subharmonic_method',legend=alt.Legend(title='Different Methods used',titleAnchor='middle',symbolSize=100))
)
line_charts = (line_chart.mark_line(opacity=0.6) + line_chart.mark_point().encode(shape='subharmonic_method'))


chart_gt = alt.Chart(df_gt).encode(
   x=alt.X('chord_label', sort=empirical_ranking_triads),
    y='normalized_value',
).mark_line(
    color='black'
)
(line_charts+chart_gt).properties(width=400,height=400,title='Overall interharmonic tension ratings for triads ranked (periods considered = 14)').configure_legend(labelLimit=1000,orient='right', direction='vertical').resolve_scale(color='shared').resolve_legend(color='shared',shape='shared')


alt.LayerChart(...)

In [121]:
df_per_chord_label.subharmonic_method.unique()

array(['Smallest_delta_t_and_choose_top_3_t_sub',
       "Smallest_delta_t_and_filter_by_smallest_t_sub_(Chan's_method?)",
       'Smallest_ratio_and_filter_by_smallest_t_sub',
       'Smallest_ratio_and_filter_by_smallest_t_sub_without_square',
       'Smallest_t_sub_and_choose_top_3_delta_t',
       'Smallest_t_sub_and_filter_by_smallest_delta_t'], dtype=object)